# Automatic Data Type Discovery

In [1]:
from scipy.io import savemat
import openml as oml
import pandas as pd
import numpy as np
import random

## 1. Heuristic Methods

In [2]:
def infer_feature_type(feature):
    """
    Infer data types for the given feature using simple logic
    Possible data types to infer: boolean, date, float, integer, string
    Feature that is not either a boolean, a date, a float or an integer, is classified as a string
    """
    data_type = ""
    types = ["date","float64","int64","string"]
    weights = [0,0,0,0] #Weights corresponding to the data types
    feature_len = len(feature)
    
    indices_number = int(0.1 * feature_len) #Number of different values to check in a feature
    indices = random.sample(range(0,feature_len), min(indices_number,feature_len)) #Array of random indices
    
    # If the feature only contains two different unique values, then infer it as boolean
    if len(pd.unique(feature)) == 2:
        data_type = "bool"
    else:
        for i in indices:
            try:
                if (len(feature[i]) <= 10 
                    and (((feature[i][2:3]=='-' or feature[i][2:3]=='/') 
                    and (feature[i][5:6]=='-' or feature[i][5:6]=='/')) 
                    or ((feature[i][4:5]=='-' or feature[i][4:5]=='/')
                    and (feature[i][7:8]=='-' or feature[i][7:8]=='/')))):
                    weights[0] += 1 #Date
                else:
                    weights[3] += 1 #String
            except (TypeError,ValueError,IndexError):
                try:
                    int(feature[i]) # numeric
                    if ('.' in str(feature[i])):
                        if isinstance(feature[i], np.float64):
                            if feature[i].is_integer():
                                weights[2] += 1 # Integer
                            else:
                                weights[1] += 1 # Float
                        else:
                            weights[1] += 1 # Float
                    else:
                        weights[2] += 1 #Integer
                except (TypeError,ValueError,IndexError):
                    weights[3] += 1 #String
#         print ("Date: {}, Float64: {}, Int64: {}, String: {}".format(weights[0],weights[1],weights[2],weights[3])) #For debugging purposes
        data_type = types[weights.index(max(weights))]
        
    return data_type

def discover_type_heuristic(data):
    """
    Automatically infer data types for each feature in the dataframe using simple logic
    ---
    input:

    data : numpy array or dataframe (numeric data needs to be 64 bit)
        
    """
#     df = pd.DataFrame(data)
#     print(df)
    result = []
    if isinstance(data, np.ndarray):
        # convert float32 to float64
        data = np.array(data, dtype='float64')
        df = pd.DataFrame(data)
    else:
        df = data

    for column in df.columns:        
        #print ("Trying to automatically infer the data type of the",column,"feature...") #For debugging purposes
        type_inferred = infer_feature_type(df[column])
        result.append(type_inferred)
        #print ("Result:",inferredType) #For debugging purposes
    return result

### 1.1 Get data from csv

In [3]:
df = pd.read_csv("datasets_csv/tips.csv")
df.head()

total_bill   tip     sex smoker  day    time  size
0       16.99  1.01  Female     No  Sun  Dinner     2
1       10.34  1.66    Male     No  Sun  Dinner     3
2       21.01  3.50    Male     No  Sun  Dinner     3
3       23.68  3.31    Male     No  Sun  Dinner     2
4       24.59  3.61  Female     No  Sun  Dinner     4

In [4]:
discover_type_heuristic(df)

['float64', 'float64', 'bool', 'bool', 'string', 'bool', 'int64']

### 1.2 Get data from openml

In [5]:
data = oml.datasets.get_dataset(1480)
Xy = data.get_data()
Xy.shape

(583, 11)

In [6]:
discover_type_heuristic(Xy)

['int64',
 'bool',
 'float64',
 'float64',
 'int64',
 'int64',
 'int64',
 'float64',
 'float64',
 'float64',
 'bool']

## 2. Bayesian Method
To apply bayesian methos, dataset needs to be parsed into tabular numeric form beforehand.

### Get data from openml

In [7]:
data = oml.datasets.get_dataset(40498)
Xy = data.get_data()
Xy.shape

(4898, 12)

### Generate mat file

In [8]:
def generate_mat(data, extra_cardinality=1):
    simple_types = discover_type_heuristic(data)
    # map simple types to meta types
    # 1: real (w positive: all real | positive | interval)
    # 2: real (w/o positive: all real | interval)
    # 3: binary data
    # 4: discrete (non-binary: categorical | ordinal | count)
    # note: for now, the implemented bayesian method version by isabel can distinguish between real, postive real, categorical and count
    # the binary data should be mapped to meta type 4 discrete instead of meta type 3 due to the limited implemented version. This may change
    # if the extended version has been implemented by isabel.
    meta_types = [] 
    for i in range(len(simple_types)):
#         print(simple_types[i])
        if simple_types[i] == "bool":
            meta_types.append(4) # may change in the future
        elif simple_types[i] == "int64" or simple_types[i] == "float64":
            if (len(np.unique(data[:,i])) < 0.02 * len(data[:,i]) and len(np.unique(data[:,i])) < 50):
                meta_types.append(4)
            else:
                if (data[:,i] > 0).all():
                    meta_types.append(1)
                else:
                    meta_types.append(2)
        else:
            meta_types.append(1)
    discrete_cardinality = [] # number of unique for discrete feature, 1 for others
    for i in range(len(meta_types)):
        if (meta_types[i] == 4):
            discrete_cardinality.append(int(np.max(data[:,i])) + extra_cardinality) 
        else:
            discrete_cardinality.append(1)
    data_dict = {'X': data,
                 'T': np.asarray(meta_types),
                 'R': np.asarray(discrete_cardinality)}
    print(data_dict)
    savemat('bayesian/data/temp/data.mat', data_dict, oned_as='row')

In [9]:
generate_mat(Xy)

{'X': array([[ 7.  ,  0.27,  0.36, ...,  0.45,  8.8 ,  3.  ],
       [ 6.3 ,  0.3 ,  0.34, ...,  0.49,  9.5 ,  3.  ],
       [ 8.1 ,  0.28,  0.4 , ...,  0.44, 10.1 ,  3.  ],
       ...,
       [ 6.5 ,  0.24,  0.19, ...,  0.46,  9.4 ,  3.  ],
       [ 5.5 ,  0.29,  0.3 , ...,  0.38, 12.8 ,  4.  ],
       [ 6.  ,  0.21,  0.38, ...,  0.32, 11.8 ,  3.  ]], dtype=float32), 'T': array([1, 1, 2, 1, 1, 1, 1, 1, 1, 1, 1, 4]), 'R': array([1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 7])}


### Call bayesian model

In [10]:
from bayesian.bin import abda

D:\Programfiles\Anaconda3\lib\site-packages\h5py\__init__.py:34: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters


In [13]:
weights = abda.main(seed=1337, dataset='bayesian/data/temp/data.mat', exp_id=None, args_output='./exp/temp/', args_miss=None, verbose=1,
         args_col_split_threshold=0.8, args_min_inst_slice=500, args_leaf_type='pm',
         args_type_param_map='spicky-prior-1', args_param_init='default', args_param_weight_init='uniform',
         args_n_iters=5, args_burn_in=4000, args_w_unif_prior=100, args_save_samples=1,
         args_ll_history=1, args_omega_prior='uniform', args_plot_iter=10, args_omega_unif_prior=10,
         args_leaf_omega_unif_prior=0.1, args_cat_unif_prior=1)


Loaded bayesian/data/temp/data.mat
	with shape: (4898, 12)
	meta-types:[1 1 2 1 1 1 1 1 1 1 1 4]
	maximal discrete cardinality: [1 1 1 1 1 1 1 1 1 1 1 7]
	meta types [<MetaType.REAL: 1> <MetaType.REAL: 1> <MetaType.REAL: 1>
 <MetaType.REAL: 1> <MetaType.REAL: 1> <MetaType.REAL: 1>
 <MetaType.REAL: 1> <MetaType.REAL: 1> <MetaType.REAL: 1>
 <MetaType.REAL: 1> <MetaType.REAL: 1> <MetaType.DISCRETE: 3>]
	domains [array([ 3.79999995, 14.19999981]), array([0.08      , 1.10000002]), array([0.        , 1.65999997]), array([ 0.60000002, 65.80000305]), array([0.009     , 0.34599999]), array([  2., 289.]), array([  9., 440.]), array([0.98711002, 1.03898001]), array([2.72000003, 3.81999993]), array([0.22      , 1.08000004]), array([ 8.        , 14.19999981]), array([0, 1, 2, 3, 4, 5, 6], dtype=int64)]
	translated discrete features (starting from 0)
MT MetaType.REAL OrderedDict([(<Type.REAL: (1, <MetaType.REAL: 1>)>, OrderedDict([(<class 'bayesian.spn.structure.leaves.parametric.Parametric.Gaussia

{'params': {'alpha': 1.9967129409128155, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F6A6F3C8>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F6A6FFD0>}
gamma fit params (10.443556298462036, 0, 0.003776674490135308)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032FB9C7400>}
{'params': {'alpha': 10.443556298462036, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032FB9C7320>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032FB9C74A8>}
gamma fit params (4.007340933194108, 0, 7.1208967527828975)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032FB9C75F8>}
{'params': {'alpha': 4.007340933194108, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma o

 0.00149421])) + 0.3333333333333333*(Geometric(V11|p=0.5)) + 0.3333333333333333*(Poisson(V11|mean=2))))))
[0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11]
Done iteration 1/5 in 0.21051156437879115


------------------
Done iteration 2/5 in 0.19114206875860873


------------------
Done iteration 3/5 in 0.1936748236427377


------------------
Done iteration 4/5 in 0.20977100200931886


------------------
Done iteration 5/5 in 0.1938804915502459


------------------
Done in 1.0259828439016019
Dumped id to ./exp/temp/data.mat\20181109-143004\global-W.pklz
Dumped id to ./exp/temp/data.mat\20181109-143004\global-type-W.pklz
seeeeeeeeeeeeeeeeeeeeeeeeeee
./exp/temp/data.mat\20181109-143004


In [14]:
weights

{0: {<Type.REAL: (1, <MetaType.REAL: 1>)>: 0.4600566083061194,
  <Type.POSITIVE: (3, <MetaType.REAL: 1>)>: 0.5399433916938805},
 1: {<Type.REAL: (1, <MetaType.REAL: 1>)>: 0.7978470462800155,
  <Type.POSITIVE: (3, <MetaType.REAL: 1>)>: 0.20215295371998454},
 2: {<Type.REAL: (1, <MetaType.REAL: 1>)>: 0.757861805905059,
  <Type.POSITIVE: (3, <MetaType.REAL: 1>)>: 0.24213819409494106},
 3: {<Type.REAL: (1, <MetaType.REAL: 1>)>: 0.2775528468893933,
  <Type.POSITIVE: (3, <MetaType.REAL: 1>)>: 0.7224471531106068},
 4: {<Type.REAL: (1, <MetaType.REAL: 1>)>: 0.09891028338710824,
  <Type.POSITIVE: (3, <MetaType.REAL: 1>)>: 0.9010897166128917},
 5: {<Type.REAL: (1, <MetaType.REAL: 1>)>: 0.008020538618635232,
  <Type.POSITIVE: (3, <MetaType.REAL: 1>)>: 0.9919794613813647},
 6: {<Type.REAL: (1, <MetaType.REAL: 1>)>: 0.000594935735371131,
  <Type.POSITIVE: (3, <MetaType.REAL: 1>)>: 0.9994050642646287},
 7: {<Type.REAL: (1, <MetaType.REAL: 1>)>: 0.9912703508764001,
  <Type.POSITIVE: (3, <MetaType.REA

## 3. Evaluation
We evaluate the bayesian method on the 30 most runs openml datasets. The ids of the 30 openml datasets are as follows: <br>
31, 1464, 334, 50, 333, 1494, 3, 1510, 1489, 37, 1479, 1487, 1063, 1471, 1467, 1480, 1068, 1492, 1050, 1462, 1046, 1049, 335, 

In [17]:
def get_statistical_type(weights):
    """
    Retrieve the key with the higher value from 'weights'
    The retrieved key is the statisical type of the corresponding feature
    """
    statistical_types = []
    for i in range(len(weights)):
#         print(max(weights[i], key=weights[i].get))
        statistical_types.append(str(max(weights[i], key=weights[i].get)))
    return statistical_types

In [18]:
def statistical_type_accurracy(ground_truth, statistical_types):
    count = 0 # number of correct predictions
    for i in range(len(ground_truth)):
        if ground_truth[i] == statistical_types[i]:
            count += 1
    return count / len(ground_truth)

In [29]:
def evaluate_bayesian(dataset_id, ground_truth, n_iters=1):
    data = oml.datasets.get_dataset(dataset_id)
    Xy = data.get_data()
    Xy.shape
    try:
        generate_mat(Xy)
        weights = abda.main(seed=1337, dataset='bayesian/data/temp/data.mat', exp_id=None, args_output='./exp/temp/', args_miss=None, verbose=1,
         args_col_split_threshold=0.8, args_min_inst_slice=500, args_leaf_type='pm',
         args_type_param_map='spicky-prior-1', args_param_init='default', args_param_weight_init='uniform',
         args_n_iters=n_iters, args_burn_in=4000, args_w_unif_prior=100, args_save_samples=1,
         args_ll_history=1, args_omega_prior='uniform', args_plot_iter=10, args_omega_unif_prior=10,
         args_leaf_omega_unif_prior=0.1, args_cat_unif_prior=1)
    except:
        generate_mat(Xy, 10)
        weights = abda.main(seed=1337, dataset='bayesian/data/temp/data.mat', exp_id=None, args_output='./exp/temp/', args_miss=None, verbose=1,
         args_col_split_threshold=0.8, args_min_inst_slice=500, args_leaf_type='pm',
         args_type_param_map='spicky-prior-1', args_param_init='default', args_param_weight_init='uniform',
         args_n_iters=n_iters, args_burn_in=4000, args_w_unif_prior=100, args_save_samples=1,
         args_ll_history=1, args_omega_prior='uniform', args_plot_iter=10, args_omega_unif_prior=10,
         args_leaf_omega_unif_prior=0.1, args_cat_unif_prior=1)
    statistical_types = get_statistical_type(weights)
    print(statistical_types)
    accuracy = statistical_type_accurracy(ground_truth, statistical_types)
    return accuracy

In [37]:
# 31
ground_truth = ['Type.CATEGORICAL', 'Type.POSITIVE', 'Type.CATEGORICAL', 'Type.CATEGORICAL', 'Type.POSITIVE',
                'Type.CATEGORICAL', 'Type.CATEGORICAL', 'Type.CATEGORICAL', 'Type.CATEGORICAL', 'Type.CATEGORICAL',
                'Type.POSITIVE', 'Type.CATEGORICAL', 'Type.POSITIVE', 'Type.CATEGORICAL', 'Type.CATEGORICAL',
                'Type.CATEGORICAL', 'Type.CATEGOTICAL', 'Type.COUNT', 'Type.CATEGORICAL',
                'Type.CATEGORICAL', 'Type.CATEGORICAL']
accuracy = evaluate_bayesian(31, ground_truth)
accuracy_5 = evaluate_bayesian(31, ground_truth, 5)
accuracy_10 = evaluate_bayesian(31, ground_truth, 10)

{'X': array([[ 0.,  6.,  4., ...,  1.,  0.,  0.],
       [ 1., 48.,  2., ...,  0.,  0.,  1.],
       [ 3., 12.,  4., ...,  0.,  0.,  0.],
       ...,
       [ 3., 12.,  2., ...,  0.,  0.,  0.],
       [ 0., 45.,  2., ...,  1.,  0.,  1.],
       [ 1., 45.,  4., ...,  0.,  0.,  0.]], dtype=float32), 'T': array([4, 1, 4, 4, 1, 4, 4, 4, 4, 4, 4, 4, 1, 4, 4, 4, 4, 4, 4, 4, 4]), 'R': array([ 4,  1,  5, 11,  1,  5,  5,  5,  4,  3,  5,  4,  1,  3,  3,  5,  4,
        3,  2,  2,  2])}

Loaded bayesian/data/temp/data.mat
	with shape: (1000, 21)
	meta-types:[4 1 4 4 1 4 4 4 4 4 4 4 1 4 4 4 4 4 4 4 4]
	maximal discrete cardinality: [ 4  1  5 11  1  5  5  5  4  3  5  4  1  3  3  5  4  3  2  2  2]
	meta types [<MetaType.DISCRETE: 3> <MetaType.REAL: 1> <MetaType.DISCRETE: 3>
 <MetaType.DISCRETE: 3> <MetaType.REAL: 1> <MetaType.DISCRETE: 3>
 <MetaType.DISCRETE: 3> <MetaType.DISCRETE: 3> <MetaType.DISCRETE: 3>
 <MetaType.DISCRETE: 3> <MetaType.DISCRETE: 3> <MetaType.DISCRETE: 3>
 <MetaType.REAL: 1> <Me

{'params': {'p': 0.5}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorBeta object at 0x00000032F9752748>}
{'params': {'mean': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F9752128>}




CATEGORICAL




1 [0. 0. 0. 0.]
{'params': {'p': array([0.14137214, 0.23492723, 0.3970894 , 0.22661123])}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorDirichlet object at 0x00000032F9752E10>}
{'params': {'p': 0.5}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorBeta object at 0x00000032F9752F98>}
{'params': {'mean': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F9752FD0>}
gamma fit params (11.487864480868597, 0, 3.091936763260361)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F9752208>}
{'params': {'alpha': 11.487864480868597, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F97524A8>}
{'params': {'l': 2}, '

{'params': {'p': array([0.03853565, 0.35645472, 0.47206166, 0.13294798])}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorDirichlet object at 0x00000032F82AFF98>}
{'params': {'p': 0.5}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorBeta object at 0x00000032F82AF8D0>}
{'params': {'mean': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F82AF860>}




CATEGORICAL




1 [0. 0. 0.]
{'params': {'p': array([0.9017341, 0.0327553, 0.0655106])}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorDirichlet object at 0x00000032F82AF198>}
{'params': {'p': 0.5}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorBeta object at 0x00000032F82AFB38>}
{'params': {'mean': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F82AFBA8>}




CATEGORICAL




1 [0. 0. 0. 0. 0.]
{'params': {'p': array([1.52215800e-01, 3.06358381e-01, 1.79190751e-01, 3.62235067e-01,
       1.92678227e-10])}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorDirichl

 1.92678227e-10])) + 0.3333333333333333*(Geometric(V15|p=0.5)) + 0.3333333333333333*(Poisson(V15|mean=2))) * TypeMixtureUnconstrained(DISCRETE, 0.3333333333333333*(Categorical(V16|p=[0.02890173 0.27745665 0.61657033 0.07707129])) + 0.3333333333333333*(Geometric(V16|p=0.5)) + 0.3333333333333333*(Poisson(V16|mean=2))) * TypeMixtureUnconstrained(DISCRETE, 0.3333333333333333*(Categorical(V17|p=[8.45857418e-01 1.54142582e-01 1.92678227e-10])) + 0.3333333333333333*(Geometric(V17|p=0.5)) + 0.3333333333333333*(Poisson(V17|mean=2))) * TypeMixtureUnconstrained(DISCRETE, 0.3333333333333333*(Categorical(V18|p=[0.74181118 0.25818882])) + 0.3333333333333333*(Geometric(V18|p=0.5)) + 0.3333333333333333*(Poisson(V18|mean=2))) * TypeMixtureUnconstrained(DISCRETE, 0.3333333333333333*(Categorical(V19|p=[0.93834297 0.06165703])) + 0.3333333333333333*(Geometric(V19|p=0.5)) + 0.3333333333333333*(Poisson(V19|mean=2))) * TypeMixtureUnconstrained(DISCRETE, 0.3333333333333333*(Categorical(V20|p=[0.75915222 0.240

{'params': {'p': 0.5}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorBeta object at 0x00000032F974CAC8>}
{'params': {'mean': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F974CE80>}




CATEGORICAL




1 [0. 0. 0. 0. 0.]
{'params': {'p': array([1.47609148e-01, 2.74428274e-01, 1.72557173e-01, 4.05405405e-01,
       2.07900208e-10])}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorDirichlet object at 0x00000032F974C860>}
{'params': {'p': 0.5}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorBeta object at 0x00000032F974C710>}
{'params': {'mean': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F974CDD8>}




CATEGORICAL




1 [0. 0. 0. 0.]
{'params': {'p': array([0.06237006, 0.25987526, 0.62993763, 0.04781705])}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorDirichlet object at 0x00000032F974CF98>}
{'params': {'p': 0.5}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorBeta object at 0x00000032F974C0B8>}
{'par

...

 1.92678227e-10])) + 0.3333333333333333*(Geometric(V15|p=0.5)) + 0.3333333333333333*(Poisson(V15|mean=2))) * TypeMixtureUnconstrained(DISCRETE, 0.3333333333333333*(Categorical(V16|p=[0.02890173 0.27745665 0.61657033 0.07707129])) + 0.3333333333333333*(Geometric(V16|p=0.5)) + 0.3333333333333333*(Poisson(V16|mean=2))) * TypeMixtureUnconstrained(DISCRETE, 0.3333333333333333*(Categorical(V17|p=[8.45857418e-01 1.54142582e-01 1.92678227e-10])) + 0.3333333333333333*(Geometric(V17|p=0.5)) + 0.3333333333333333*(Poisson(V17|mean=2))) * TypeMixtureUnconstrained(DISCRETE, 0.3333333333333333*(Categorical(V18|p=[0.74181118 0.25818882])) + 0.3333333333333333*(Geometric(V18|p=0.5)) + 0.3333333333333333*(Poisson(V18|mean=2))) * TypeMixtureUnconstrained(DISCRETE, 0.3333333333333333*(Categorical(V19|p=[0.93834297 0.06165703])) + 0.3333333333333333*(Geometric(V19|p=0.5)) + 0.3333333333333333*(Poisson(V19|mean=2))) * TypeMixtureUnconstrained(DISCRETE, 0.3333333333333333*(Categorical(V20|p=[0.75915222 0.240

{'params': {'mean': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F65B7358>}




CATEGORICAL




1 [0. 0. 0. 0. 0.]
{'params': {'p': array([0.07068607, 0.15176715, 0.30769231, 0.19334719, 0.27650728])}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorDirichlet object at 0x00000032F65B7518>}
{'params': {'p': 0.5}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorBeta object at 0x00000032F65B7438>}
{'params': {'mean': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F65B74E0>}




CATEGORICAL




1 [0. 0. 0. 0. 0.]
{'params': {'p': array([1.47609148e-01, 2.74428274e-01, 1.72557173e-01, 4.05405405e-01,
       2.07900208e-10])}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorDirichlet object at 0x00000032F65B7048>}
{'params': {'p': 0.5}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorBeta object at 0x00000032F65B7CF8>}
{'params': {'mean': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x0000003

{'params': {'p': 0.5}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorBeta object at 0x00000032F975E6D8>}
{'params': {'mean': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F97524A8>}
gamma fit params (4.758746032033568, 0, 320.19696377395746)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F9752710>}
{'params': {'alpha': 4.758746032033568, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F9752278>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F9752EB8>}




CATEGORICAL




1 [0. 0. 0. 0. 0.]
{'params': {'p': array([0.62427746, 0.09441233, 0.07129094, 0.05780347, 0.1522158 ])}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorDirichlet object at 0x00000032F9752BA8>}
{'params': {'p': 0.5}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorBeta object at 0x00000032F9752AC8>}
{'params': 

{'params': {'mean': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F82AF3C8>}
True True True
True True True
(0.481*((TypeMixtureUnconstrained(DISCRETE, 0.3333333333333333*(Categorical(V0|p=[0.28066528 0.30561331 0.03950104 0.37422037])) + 0.3333333333333333*(Geometric(V0|p=0.5)) + 0.3333333333333333*(Poisson(V0|mean=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V1|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V1|alpha=6.561670814774057;beta=1)) + 0.3333333333333333*(Exponential(V1|l=2))) * TypeMixtureUnconstrained(DISCRETE, 0.3333333333333333*(Categorical(V2|p=[0.06029106 0.05197505 0.48648649 0.13305613 0.26819127])) + 0.3333333333333333*(Geometric(V2|p=0.5)) + 0.3333333333333333*(Poisson(V2|mean=2))) * TypeMixtureUnconstrained(DISCRETE, 0.3333333333333333*(Categorical(V3|p=[1.85031185e-01 1.82952183e-01 1.87110187e-01 2.20374220e-01
 4.15800436e-03 1.87110189e-02 4.57380458e-02 2.07900207e-10
 2.07900207e-10 1.35135135e-01 2.079002

 1.92678227e-10])) + 0.3333333333333333*(Geometric(V15|p=0.5)) + 0.3333333333333333*(Poisson(V15|mean=2))) * TypeMixtureUnconstrained(DISCRETE, 0.3333333333333333*(Categorical(V16|p=[0.02890173 0.27745665 0.61657033 0.07707129])) + 0.3333333333333333*(Geometric(V16|p=0.5)) + 0.3333333333333333*(Poisson(V16|mean=2))) * TypeMixtureUnconstrained(DISCRETE, 0.3333333333333333*(Categorical(V17|p=[8.45857418e-01 1.54142582e-01 1.92678227e-10])) + 0.3333333333333333*(Geometric(V17|p=0.5)) + 0.3333333333333333*(Poisson(V17|mean=2))) * TypeMixtureUnconstrained(DISCRETE, 0.3333333333333333*(Categorical(V18|p=[0.74181118 0.25818882])) + 0.3333333333333333*(Geometric(V18|p=0.5)) + 0.3333333333333333*(Poisson(V18|mean=2))) * TypeMixtureUnconstrained(DISCRETE, 0.3333333333333333*(Categorical(V19|p=[0.93834297 0.06165703])) + 0.3333333333333333*(Geometric(V19|p=0.5)) + 0.3333333333333333*(Poisson(V19|mean=2))) * TypeMixtureUnconstrained(DISCRETE, 0.3333333333333333*(Categorical(V20|p=[0.75915222 0.240

In [38]:
print("Accuracy of the inferred statistical types is {}".format(accuracy))
print("Accuracy of the inferred statistical types after 5 iterations is {}".format(accuracy_5))
print("Accuracy of the inferred statistical types after 10 iterations is {}".format(accuracy_10))

Accuracy of the inferred statistical types is 0.5238095238095238
Accuracy of the inferred statistical types after 5 iterations is 0.8571428571428571
Accuracy of the inferred statistical types after 10 iterations is 0.8095238095238095


In [39]:
# 1464
ground_truth = ['Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.CATEGORICAL']
accuracy = evaluate_bayesian(1464, ground_truth)
accuracy_5 = evaluate_bayesian(1464, ground_truth, 5)
accuracy_10 = evaluate_bayesian(1464, ground_truth, 10)

{'X': array([[2.00e+00, 5.00e+01, 1.25e+04, 9.80e+01, 1.00e+00],
       [0.00e+00, 1.30e+01, 3.25e+03, 2.80e+01, 1.00e+00],
       [1.00e+00, 1.60e+01, 4.00e+03, 3.50e+01, 1.00e+00],
       ...,
       [2.30e+01, 3.00e+00, 7.50e+02, 6.20e+01, 0.00e+00],
       [3.90e+01, 1.00e+00, 2.50e+02, 3.90e+01, 0.00e+00],
       [7.20e+01, 1.00e+00, 2.50e+02, 7.20e+01, 0.00e+00]], dtype=float32), 'T': array([2, 1, 1, 1, 4]), 'R': array([1, 1, 1, 1, 2])}

Loaded bayesian/data/temp/data.mat
	with shape: (748, 5)
	meta-types:[2 1 1 1 4]
	maximal discrete cardinality: [1 1 1 1 2]
	meta types [<MetaType.REAL: 1> <MetaType.REAL: 1> <MetaType.REAL: 1>
 <MetaType.REAL: 1> <MetaType.DISCRETE: 3>]
	domains [array([ 0., 74.]), array([ 1., 50.]), array([  250., 12500.]), array([ 2., 98.]), array([0, 1], dtype=int64)]
	translated discrete features (starting from 0)
MT MetaType.REAL OrderedDict([(<Type.REAL: (1, <MetaType.REAL: 1>)>, OrderedDict([(<class 'bayesian.spn.structure.leaves.parametric.Parametric.Gau

(0.5*((TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V0|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V0|alpha=1.1;beta=1)) + 0.3333333333333333*(Exponential(V0|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V1|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V1|alpha=3.2188686184485946;beta=1)) + 0.3333333333333333*(Exponential(V1|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V2|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V2|alpha=3.2188686184485946;beta=1)) + 0.3333333333333333*(Exponential(V2|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V3|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V3|alpha=5.020117630242249;beta=1)) + 0.3333333333333333*(Exponential(V3|l=2))) * TypeMixtureUnconstrained(DISCRETE, 0.3333333333333333*(Categorical(V4|p=[0.68181818 0.31818182])) + 0.3333333333333333*(Geometric(V4|p=0.5)) + 0.3333333333333333*(Poisson(V4|mean=2))))) + 0.5*((TypeMixtureUnconstrained(REAL, 0.3333333333333333*(

{'params': {'alpha': 1.582934342854446, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F6A07BE0>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F6A07198>}




CATEGORICAL




1 [0. 0.]
{'params': {'p': array([0.84224599, 0.15775401])}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorDirichlet object at 0x00000032F6A072B0>}
{'params': {'p': 0.5}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorBeta object at 0x00000032F6A076D8>}
{'params': {'mean': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F6A07160>}
True True True
True True True
(0.5*((TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V0|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V0|alpha=1.1;beta=1)) + 0.3333333333333333*(Exponential(V0|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V1|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V1|alpha=3.2188686184485946;beta=1)) + 0

{'params': {'alpha': 3.9901332638498364, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F65B7B70>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F65B7978>}
gamma fit params (3.990133263849819, 0, 122.79621497136223)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F6A07160>}
{'params': {'alpha': 3.990133263849819, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F6A07588>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F6A07DD8>}
gamma fit params (1.582934342854446, 0, 11.40000191853432)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F6A07978>}
{'params': {'alpha': 1.582934342854446, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object

In [40]:
print("Accuracy of the inferred statistical types is {}".format(accuracy))
print("Accuracy of the inferred statistical types after 5 iterations is {}".format(accuracy_5))
print("Accuracy of the inferred statistical types after 10 iterations is {}".format(accuracy_10))

Accuracy of the inferred statistical types is 1.0
Accuracy of the inferred statistical types after 5 iterations is 1.0
Accuracy of the inferred statistical types after 10 iterations is 1.0


In [43]:
# 334
ground_truth = ['Type.CATEGORICAL', 'Type.CATEGORICAL', 'Type.CATEGORICAL', 'Type.CATEGORICAL', 'Type.CATEGORICAL', 'Type.CATEGORICAL', 'Type.CATEGORICAL']
accuracy = evaluate_bayesian(334, ground_truth)
accuracy_5 = evaluate_bayesian(334, ground_truth, 5)
accuracy_10 = evaluate_bayesian(334, ground_truth, 10)

{'X': array([[0., 0., 0., ..., 0., 1., 1.],
       [0., 0., 0., ..., 0., 3., 0.],
       [0., 0., 0., ..., 1., 0., 0.],
       ...,
       [0., 2., 2., ..., 2., 2., 1.],
       [0., 2., 2., ..., 2., 3., 0.],
       [0., 2., 2., ..., 2., 3., 1.]], dtype=float32), 'T': array([4, 4, 4, 4, 4, 4, 4]), 'R': array([2, 3, 3, 2, 3, 4, 2])}

Loaded bayesian/data/temp/data.mat
	with shape: (601, 7)
	meta-types:[4 4 4 4 4 4 4]
	maximal discrete cardinality: [2 3 3 2 3 4 2]
	meta types [<MetaType.DISCRETE: 3> <MetaType.DISCRETE: 3> <MetaType.DISCRETE: 3>
 <MetaType.DISCRETE: 3> <MetaType.DISCRETE: 3> <MetaType.DISCRETE: 3>
 <MetaType.DISCRETE: 3>]
	domains [array([0, 1], dtype=int64), array([0, 1, 2], dtype=int64), array([0, 1, 2], dtype=int64), array([0, 1], dtype=int64), array([0, 1, 2], dtype=int64), array([0, 1, 2, 3], dtype=int64), array([0, 1], dtype=int64)]
	translated discrete features (starting from 0)
MT MetaType.REAL OrderedDict([(<Type.REAL: (1, <MetaType.REAL: 1>)>, OrderedDict([(<clas

(0.5008319467554077*((TypeMixtureUnconstrained(DISCRETE, 0.3333333333333333*(Categorical(V6|p=[3.32225913e-10 1.00000000e+00])) + 0.3333333333333333*(Geometric(V6|p=0.5)) + 0.3333333333333333*(Poisson(V6|mean=2))) * TypeMixtureUnconstrained(DISCRETE, 0.3333333333333333*(Categorical(V0|p=[0.63455149 0.36544851])) + 0.3333333333333333*(Geometric(V0|p=0.5)) + 0.3333333333333333*(Poisson(V0|mean=2))) * TypeMixtureUnconstrained(DISCRETE, 0.3333333333333333*(Categorical(V1|p=[0.33222591 0.33554817 0.33222591])) + 0.3333333333333333*(Geometric(V1|p=0.5)) + 0.3333333333333333*(Poisson(V1|mean=2))) * TypeMixtureUnconstrained(DISCRETE, 0.3333333333333333*(Categorical(V2|p=[0.33887043 0.33887043 0.32225914])) + 0.3333333333333333*(Geometric(V2|p=0.5)) + 0.3333333333333333*(Poisson(V2|mean=2))) * TypeMixtureUnconstrained(DISCRETE, 0.3333333333333333*(Categorical(V3|p=[0.50166113 0.49833887])) + 0.3333333333333333*(Geometric(V3|p=0.5)) + 0.3333333333333333*(Poisson(V3|mean=2))) * TypeMixtureUnconst

{'params': {'p': 0.5}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorBeta object at 0x00000032F65B7978>}
{'params': {'mean': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F65B77B8>}




CATEGORICAL




1 [0. 0. 0. 0.]
{'params': {'p': array([0.24252492, 0.25249169, 0.26578073, 0.23920266])}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorDirichlet object at 0x00000032F65B7278>}
{'params': {'p': 0.5}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorBeta object at 0x00000032F65B7E10>}
{'params': {'mean': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F65B7898>}




CATEGORICAL




1 [0. 0.]
{'params': {'p': array([0.68, 0.32])}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorDirichlet object at 0x00000032F65A7710>}
{'params': {'p': 0.5}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorBeta object at 0x00000032F7CBCC88>}
{'params': {'mean': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at

MT MetaType.DISCRETE OrderedDict([(<Type.CATEGORICAL: (4, <MetaType.DISCRETE: 3>)>, {<class 'bayesian.spn.structure.leaves.parametric.Parametric.Categorical'>: {'params': {'p': None}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorDirichlet object at 0x00000032F5C98860>}}), (<Type.COUNT: (6, <MetaType.DISCRETE: 3>)>, OrderedDict([(<class 'bayesian.spn.structure.leaves.parametric.Parametric.Geometric'>, {'params': {'p': 0.5}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorBeta object at 0x00000032F7FF3240>}), (<class 'bayesian.spn.structure.leaves.parametric.Parametric.Poisson'>, {'params': {'mean': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F7B20A90>})]))])




CATEGORICAL




1 [0. 0.]
{'params': {'p': array([3.32225913e-10, 1.00000000e+00])}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorDirichlet object at 0x00000032F65B77B8>}
{'params': {'p': 0.5}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorBeta object at 0x00000032F65B7358>}
{'

(0.5008319467554077*((TypeMixtureUnconstrained(DISCRETE, 0.3333333333333333*(Categorical(V6|p=[3.32225913e-10 1.00000000e+00])) + 0.3333333333333333*(Geometric(V6|p=0.5)) + 0.3333333333333333*(Poisson(V6|mean=2))) * TypeMixtureUnconstrained(DISCRETE, 0.3333333333333333*(Categorical(V0|p=[0.63455149 0.36544851])) + 0.3333333333333333*(Geometric(V0|p=0.5)) + 0.3333333333333333*(Poisson(V0|mean=2))) * TypeMixtureUnconstrained(DISCRETE, 0.3333333333333333*(Categorical(V1|p=[0.33222591 0.33554817 0.33222591])) + 0.3333333333333333*(Geometric(V1|p=0.5)) + 0.3333333333333333*(Poisson(V1|mean=2))) * TypeMixtureUnconstrained(DISCRETE, 0.3333333333333333*(Categorical(V2|p=[0.33887043 0.33887043 0.32225914])) + 0.3333333333333333*(Geometric(V2|p=0.5)) + 0.3333333333333333*(Poisson(V2|mean=2))) * TypeMixtureUnconstrained(DISCRETE, 0.3333333333333333*(Categorical(V3|p=[0.50166113 0.49833887])) + 0.3333333333333333*(Geometric(V3|p=0.5)) + 0.3333333333333333*(Poisson(V3|mean=2))) * TypeMixtureUnconst

In [44]:
print("Accuracy of the inferred statistical types is {}".format(accuracy))
print("Accuracy of the inferred statistical types after 5 iterations is {}".format(accuracy_5))
print("Accuracy of the inferred statistical types after 10 iterations is {}".format(accuracy_10))

Accuracy of the inferred statistical types is 0.0
Accuracy of the inferred statistical types after 5 iterations is 0.42857142857142855
Accuracy of the inferred statistical types after 10 iterations is 0.5714285714285714


In [46]:
# 50
ground_truth = ['Type.CATEGORICAL', 'Type.CATEGORICAL', 'Type.CATEGORICAL', 'Type.CATEGORICAL', 'Type.CATEGORICAL',
                'Type.CATEGORICAL', 'Type.CATEGORICAL', 'Type.CATEGORICAL', 'Type.CATEGORICAL', 'Type.CATEGORICAL']
accuracy = evaluate_bayesian(50, ground_truth)
accuracy_5 = evaluate_bayesian(50, ground_truth, 5)
accuracy_10 = evaluate_bayesian(50, ground_truth, 10)

{'X': array([[2., 2., 2., ..., 1., 1., 1.],
       [2., 2., 2., ..., 2., 1., 1.],
       [2., 2., 2., ..., 1., 2., 1.],
       ...,
       [1., 2., 1., ..., 1., 2., 0.],
       [1., 2., 1., ..., 1., 2., 0.],
       [1., 1., 2., ..., 2., 2., 0.]], dtype=float32), 'T': array([4, 4, 4, 4, 4, 4, 4, 4, 4, 4]), 'R': array([3, 3, 3, 3, 3, 3, 3, 3, 3, 2])}

Loaded bayesian/data/temp/data.mat
	with shape: (958, 10)
	meta-types:[4 4 4 4 4 4 4 4 4 4]
	maximal discrete cardinality: [3 3 3 3 3 3 3 3 3 2]
	meta types [<MetaType.DISCRETE: 3> <MetaType.DISCRETE: 3> <MetaType.DISCRETE: 3>
 <MetaType.DISCRETE: 3> <MetaType.DISCRETE: 3> <MetaType.DISCRETE: 3>
 <MetaType.DISCRETE: 3> <MetaType.DISCRETE: 3> <MetaType.DISCRETE: 3>
 <MetaType.DISCRETE: 3>]
	domains [array([0, 1, 2], dtype=int64), array([0, 1, 2], dtype=int64), array([0, 1, 2], dtype=int64), array([0, 1, 2], dtype=int64), array([0, 1, 2], dtype=int64), array([0, 1, 2], dtype=int64), array([0, 1, 2], dtype=int64), array([0, 1, 2], dtype=int64)

{'params': {'mean': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F975E748>}




CATEGORICAL




1 [0. 0. 0.]
{'params': {'p': array([0.23493976, 0.30421687, 0.46084337])}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorDirichlet object at 0x00000032F975ED30>}
{'params': {'p': 0.5}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorBeta object at 0x00000032F975EFD0>}
{'params': {'mean': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F975EEF0>}




CATEGORICAL




1 [0. 0. 0.]
{'params': {'p': array([0.14457831, 0.57831325, 0.27710843])}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorDirichlet object at 0x00000032F975E860>}
{'params': {'p': 0.5}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorBeta object at 0x00000032F975E550>}
{'params': {'mean': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F975E898>}




CATEGORICAL




1 [0. 0. 0.]
{'params': {'p': array([0.23493976, 0.3042

MT MetaType.REAL OrderedDict([(<Type.REAL: (1, <MetaType.REAL: 1>)>, OrderedDict([(<class 'bayesian.spn.structure.leaves.parametric.Parametric.Gaussian'>, {'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032EF231160>})])), (<Type.POSITIVE: (3, <MetaType.REAL: 1>)>, OrderedDict([(<class 'bayesian.spn.structure.leaves.parametric.Parametric.Gamma'>, {'params': {'alpha': None, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032EF231550>}), (<class 'bayesian.spn.structure.leaves.parametric.Parametric.Exponential'>, {'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F27B6128>})]))])
MT MetaType.DISCRETE OrderedDict([(<Type.CATEGORICAL: (4, <MetaType.DISCRETE: 3>)>, {<class 'bayesian.spn.structure.leaves.parametric.Parametric.Categorical'>: {'params': {'p': None}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorDirichlet object at 0x0000

{'params': {'p': 0.5}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorBeta object at 0x00000032F975E240>}
{'params': {'mean': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F975E630>}




CATEGORICAL




1 [0. 0. 0.]
{'params': {'p': array([0.18975904, 0.43975904, 0.37048193])}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorDirichlet object at 0x00000032F975EA58>}
{'params': {'p': 0.5}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorBeta object at 0x00000032F975EE80>}
{'params': {'mean': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F975E3C8>}




CATEGORICAL




1 [0. 0. 0.]
{'params': {'p': array([0.23493976, 0.30421687, 0.46084337])}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorDirichlet object at 0x00000032F975E940>}
{'params': {'p': 0.5}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorBeta object at 0x00000032F975ED68>}
{'params': {'mean': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGam

MT MetaType.DISCRETE OrderedDict([(<Type.CATEGORICAL: (4, <MetaType.DISCRETE: 3>)>, {<class 'bayesian.spn.structure.leaves.parametric.Parametric.Categorical'>: {'params': {'p': None}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorDirichlet object at 0x00000032F5C98860>}}), (<Type.COUNT: (6, <MetaType.DISCRETE: 3>)>, OrderedDict([(<class 'bayesian.spn.structure.leaves.parametric.Parametric.Geometric'>, {'params': {'p': 0.5}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorBeta object at 0x00000032F7FF3240>}), (<class 'bayesian.spn.structure.leaves.parametric.Parametric.Poisson'>, {'params': {'mean': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F7B20A90>})]))])




CATEGORICAL




1 [0. 0.]
{'params': {'p': array([1.59744409e-10, 1.00000000e+00])}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorDirichlet object at 0x00000032F65B7E10>}
{'params': {'p': 0.5}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorBeta object at 0x00000032F65B75F8>}
{'

{'params': {'p': array([0.23493976, 0.30421687, 0.46084337])}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorDirichlet object at 0x00000032FB9C76A0>}
{'params': {'p': 0.5}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorBeta object at 0x00000032FB9C7710>}
{'params': {'mean': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032FB9C78D0>}




CATEGORICAL




1 [0. 0. 0.]
{'params': {'p': array([0.18975904, 0.43975904, 0.37048193])}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorDirichlet object at 0x00000032F801D908>}
{'params': {'p': 0.5}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorBeta object at 0x00000032F801D128>}
{'params': {'mean': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F801D7B8>}
True True True
True True True
(0.6534446764091858*((TypeMixtureUnconstrained(DISCRETE, 0.3333333333333333*(Categorical(V9|p=[1.59744409e-10 1.00000000e+00])) + 0.3333333333333333*(Geometric(V9|p=0.5)) + 0.33333333333333

In [47]:
print("Accuracy of the inferred statistical types is {}".format(accuracy))
print("Accuracy of the inferred statistical types after 5 iterations is {}".format(accuracy_5))
print("Accuracy of the inferred statistical types after 10 iterations is {}".format(accuracy_10))

Accuracy of the inferred statistical types is 0.0
Accuracy of the inferred statistical types after 5 iterations is 0.3
Accuracy of the inferred statistical types after 10 iterations is 0.7


In [49]:
# 333
ground_truth = ['Type.CATEGORICAL', 'Type.CATEGORICAL', 'Type.CATEGORICAL', 'Type.CATEGORICAL', 'Type.CATEGORICAL', 'Type.CATEGORICAL', 'Type.CATEGORICAL']
accuracy = evaluate_bayesian(333, ground_truth)
accuracy_5 = evaluate_bayesian(333, ground_truth, 5)
accuracy_10 = evaluate_bayesian(333, ground_truth, 10)

{'X': array([[1., 0., 0., ..., 0., 2., 0.],
       [1., 0., 0., ..., 0., 2., 1.],
       [1., 0., 0., ..., 2., 1., 0.],
       ...,
       [1., 2., 2., ..., 2., 2., 1.],
       [1., 2., 2., ..., 2., 3., 0.],
       [1., 2., 2., ..., 2., 3., 1.]], dtype=float32), 'T': array([4, 4, 4, 4, 4, 4, 4]), 'R': array([2, 3, 3, 2, 3, 4, 2])}

Loaded bayesian/data/temp/data.mat
	with shape: (556, 7)
	meta-types:[4 4 4 4 4 4 4]
	maximal discrete cardinality: [2 3 3 2 3 4 2]
	meta types [<MetaType.DISCRETE: 3> <MetaType.DISCRETE: 3> <MetaType.DISCRETE: 3>
 <MetaType.DISCRETE: 3> <MetaType.DISCRETE: 3> <MetaType.DISCRETE: 3>
 <MetaType.DISCRETE: 3>]
	domains [array([0, 1], dtype=int64), array([0, 1, 2], dtype=int64), array([0, 1, 2], dtype=int64), array([0, 1], dtype=int64), array([0, 1, 2], dtype=int64), array([0, 1, 2, 3], dtype=int64), array([0, 1], dtype=int64)]
	translated discrete features (starting from 0)
MT MetaType.REAL OrderedDict([(<Type.REAL: (1, <MetaType.REAL: 1>)>, OrderedDict([(<clas

(0.4892086330935252*((TypeMixtureUnconstrained(DISCRETE, 0.3333333333333333*(Categorical(V6|p=[1.00000000e+00 3.67647059e-10])) + 0.3333333333333333*(Geometric(V6|p=0.5)) + 0.3333333333333333*(Poisson(V6|mean=2))) * TypeMixtureUnconstrained(DISCRETE, 0.3333333333333333*(Categorical(V0|p=[0.49632353 0.50367647])) + 0.3333333333333333*(Geometric(V0|p=0.5)) + 0.3333333333333333*(Poisson(V0|mean=2))) * TypeMixtureUnconstrained(DISCRETE, 0.3333333333333333*(Categorical(V1|p=[0.34558824 0.34191176 0.3125    ])) + 0.3333333333333333*(Geometric(V1|p=0.5)) + 0.3333333333333333*(Poisson(V1|mean=2))) * TypeMixtureUnconstrained(DISCRETE, 0.3333333333333333*(Categorical(V2|p=[0.32352941 0.33455882 0.34191176])) + 0.3333333333333333*(Geometric(V2|p=0.5)) + 0.3333333333333333*(Poisson(V2|mean=2))) * TypeMixtureUnconstrained(DISCRETE, 0.3333333333333333*(Categorical(V3|p=[0.51102941 0.48897059])) + 0.3333333333333333*(Geometric(V3|p=0.5)) + 0.3333333333333333*(Poisson(V3|mean=2))) * TypeMixtureUnconst

{'params': {'p': 0.5}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorBeta object at 0x00000032F975E6A0>}
{'params': {'mean': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F975ED30>}




CATEGORICAL




1 [0. 0. 0. 0.]
{'params': {'p': array([0.25735294, 0.24632353, 0.24632353, 0.25      ])}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorDirichlet object at 0x00000032F975ED68>}
{'params': {'p': 0.5}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorBeta object at 0x00000032F975E048>}
{'params': {'mean': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F975E2E8>}




CATEGORICAL




1 [0. 0.]
{'params': {'p': array([0.50352113, 0.49647887])}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorDirichlet object at 0x00000032F975E7F0>}
{'params': {'p': 0.5}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorBeta object at 0x00000032F975E748>}
{'params': {'mean': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGam

MT MetaType.DISCRETE OrderedDict([(<Type.CATEGORICAL: (4, <MetaType.DISCRETE: 3>)>, {<class 'bayesian.spn.structure.leaves.parametric.Parametric.Categorical'>: {'params': {'p': None}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorDirichlet object at 0x00000032F5C98860>}}), (<Type.COUNT: (6, <MetaType.DISCRETE: 3>)>, OrderedDict([(<class 'bayesian.spn.structure.leaves.parametric.Parametric.Geometric'>, {'params': {'p': 0.5}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorBeta object at 0x00000032F7FF3240>}), (<class 'bayesian.spn.structure.leaves.parametric.Parametric.Poisson'>, {'params': {'mean': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F7B20A90>})]))])




CATEGORICAL




1 [0. 0.]
{'params': {'p': array([1.00000000e+00, 3.67647059e-10])}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorDirichlet object at 0x00000032F6A07630>}
{'params': {'p': 0.5}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorBeta object at 0x00000032F6A07710>}
{'

(0.4892086330935252*((TypeMixtureUnconstrained(DISCRETE, 0.3333333333333333*(Categorical(V6|p=[1.00000000e+00 3.67647059e-10])) + 0.3333333333333333*(Geometric(V6|p=0.5)) + 0.3333333333333333*(Poisson(V6|mean=2))) * TypeMixtureUnconstrained(DISCRETE, 0.3333333333333333*(Categorical(V0|p=[0.49632353 0.50367647])) + 0.3333333333333333*(Geometric(V0|p=0.5)) + 0.3333333333333333*(Poisson(V0|mean=2))) * TypeMixtureUnconstrained(DISCRETE, 0.3333333333333333*(Categorical(V1|p=[0.34558824 0.34191176 0.3125    ])) + 0.3333333333333333*(Geometric(V1|p=0.5)) + 0.3333333333333333*(Poisson(V1|mean=2))) * TypeMixtureUnconstrained(DISCRETE, 0.3333333333333333*(Categorical(V2|p=[0.32352941 0.33455882 0.34191176])) + 0.3333333333333333*(Geometric(V2|p=0.5)) + 0.3333333333333333*(Poisson(V2|mean=2))) * TypeMixtureUnconstrained(DISCRETE, 0.3333333333333333*(Categorical(V3|p=[0.51102941 0.48897059])) + 0.3333333333333333*(Geometric(V3|p=0.5)) + 0.3333333333333333*(Poisson(V3|mean=2))) * TypeMixtureUnconst

In [50]:
print("Accuracy of the inferred statistical types is {}".format(accuracy))
print("Accuracy of the inferred statistical types after 5 iterations is {}".format(accuracy_5))
print("Accuracy of the inferred statistical types after 10 iterations is {}".format(accuracy_10))

Accuracy of the inferred statistical types is 0.0
Accuracy of the inferred statistical types after 5 iterations is 0.14285714285714285
Accuracy of the inferred statistical types after 10 iterations is 0.42857142857142855


In [53]:
# 1494
ground_truth = ['Type.POSITIVE', 'Type.POSITIVE', 'Type.COUNT', 'Type.POSITIVE', 'Type.POSITIVE', 
                'Type.COUNT', 'Type.COUNT', 'Type.POSITIVE', 'Type.COUNT', 'Type.COUNT', 
                'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 
                'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.COUNT', 'Type.COUNT', 
                'Type.COUNT', 'Type.POSITIVE', 'Type.COUNT', 'Type.POSITIVE', 'Type.POSITIVE', 
                'Type.POSITIVE', 'Type.REAL', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE',
                'Type.POSITIVE', 'Type.COUNT', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 
                'Type.POSITIVE', 'Type.POSITIVE', 'Type.COUNT', 'Type.POSITIVE', 'Type.COUNT', 
                'Type.COUNT', 'Type.CATEGORICAL']
accuracy = evaluate_bayesian(1494, ground_truth)
accuracy_5 = evaluate_bayesian(1494, ground_truth, 5)
accuracy_10 = evaluate_bayesian(1494, ground_truth, 10)

{'X': array([[3.919 , 2.6909, 0.    , ..., 0.    , 0.    , 1.    ],
       [4.17  , 2.1144, 0.    , ..., 0.    , 0.    , 1.    ],
       [3.932 , 3.2512, 0.    , ..., 0.    , 0.    , 1.    ],
       ...,
       [4.869 , 1.767 , 0.    , ..., 1.    , 0.    , 0.    ],
       [5.158 , 1.6914, 2.    , ..., 0.    , 1.    , 0.    ],
       [5.076 , 2.6588, 2.    , ..., 0.    , 2.    , 0.    ]],
      dtype=float32), 'T': array([1, 1, 4, 4, 4, 4, 4, 2, 4, 4, 4, 2, 1, 2, 1, 2, 1, 1, 4, 4, 4, 1,
       4, 4, 4, 4, 1, 2, 4, 2, 1, 4, 4, 4, 4, 1, 1, 4, 1, 4, 4, 4]), 'R': array([  1,   1,  13,   4,  37,  14,  19,   1,  25,  13,  45,   1,   1,
         1,   1,   1,   1,   1,   3,   4,   4,   1, 148,   2,   2,   4,
         1,   1,   2,   1,   1,   9,  13,  19,   8,   1,   1,   9,   1,
         5,  28,   2])}

Loaded bayesian/data/temp/data.mat
	with shape: (1055, 42)
	meta-types:[1 1 4 4 4 4 4 2 4 4 4 2 1 2 1 2 1 1 4 4 4 1 4 4 4 4 1 2 4 2 1 4 4 4 4 1 1
 4 1 4 4 4]
	maximal discrete cardinality: [  1 

D:\Programfiles\Anaconda3\lib\site-packages\sklearn\cross_decomposition\pls_.py:79: ConvergenceWarning: Maximum number of iterations reached
  ConvergenceWarning)


gamma fit params (261.98377952482775, 0, 0.01958256442501167)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F9752668>}
{'params': {'alpha': 261.98377952482775, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F9752748>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F9752F98>}




CATEGORICAL




1 [0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.]
{'params': {'p': array([2.69097222e-01, 2.60416668e-02, 2.20486111e-01, 1.85763888e-01,
       1.52777777e-01, 3.64583334e-02, 5.20833333e-02, 1.21527779e-02,
       1.73611112e-02, 8.68055570e-03, 5.20833349e-03, 1.73611111e-10,
       8.68055570e-03, 1.73611111e-10, 1.73611128e-03, 1.73611111e-10,
       1.73611128e-03, 1.73611111e-10, 1.73611128e-03])}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorDirichlet object at 0x00000032F82BC8D0>}
{'params': {'p': 0.5}, 

       2.08768267e-10])}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorDirichlet object at 0x00000032F82DDA58>}
{'params': {'p': 0.5}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorBeta object at 0x00000032F82DD978>}
{'params': {'mean': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F82DD128>}




CATEGORICAL




1 [0. 0. 0. 0.]
{'params': {'p': array([9.79123173e-01, 1.87891442e-02, 2.08768288e-03, 2.08768267e-10])}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorDirichlet object at 0x00000032F82DD240>}
{'params': {'p': 0.5}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorBeta object at 0x00000032F82DD828>}
{'params': {'mean': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F82DD278>}




CATEGORICAL




1 [0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.]
{'params': {'p': array([8.03757823e-01, 8.55949891e-02, 7.72442585e-02, 1.25260961e-02,
 

{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032FA2EA4A8>}
{'params': {'alpha': 1.1, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032FA2EAE80>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032FA2EA080>}
gamma fit params (858.4060291534967, 0, 0.0011682112534109057)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032FA2EA6A0>}
{'params': {'alpha': 858.4060291534967, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032FA2EA6D8>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032FA2EAFD0>}
gamma fit params (3804.9161848525623, 0, 0.0002997352870800073)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x0000

...

{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F82A9048>}
{'params': {'alpha': 398.52224924819643, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F82A9A90>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F82A9D30>}
gamma fit params (27.910037280238196, 0, 0.10700371979994998)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F82A9128>}
{'params': {'alpha': 27.910037280238196, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F82A9E10>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F82A9A58>}




CATEGORICAL




1 [0. 0.]
{'params': {'p': array([3.03030301e-09, 9.99999997e-01])}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorDirichlet object at 0x00000032F

{'params': {'p': array([0.68100358, 0.31899642])}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorDirichlet object at 0x00000032F7CBC550>}
{'params': {'p': 0.5}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorBeta object at 0x00000032F7CBC208>}
{'params': {'mean': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F9763048>}




CATEGORICAL




1 [0. 0. 0. 0. 0. 0. 0. 0. 0.]
{'params': {'p': array([9.39068098e-01, 1.43369179e-02, 1.79211473e-02, 3.58422938e-10,
       1.43369179e-02, 3.58422938e-10, 1.07526885e-02, 3.58422938e-10,
       3.58422974e-03])}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorDirichlet object at 0x00000032F97634A8>}
{'params': {'p': 0.5}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorBeta object at 0x00000032F9763358>}
{'params': {'mean': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F9763F60>}




CATEGORICAL




1 [0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.]
{'params': {'p': array([3.90

       3.36700320e-10, 3.36700320e-10, 3.36700320e-10, 3.36700320e-10])}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorDirichlet object at 0x00000032F82AF8D0>}
{'params': {'p': 0.5}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorBeta object at 0x00000032F82AF320>}
{'params': {'mean': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F82AF5C0>}




CATEGORICAL




1 [0. 0.]
{'params': {'p': array([0.86868687, 0.13131313])}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorDirichlet object at 0x00000032F65A7F28>}
{'params': {'p': 0.5}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorBeta object at 0x00000032F65A7908>}
{'params': {'mean': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F65A77B8>}




CATEGORICAL




1 [0. 0. 0. 0. 0. 0. 0. 0. 0.]
{'params': {'p': array([8.88888887e-01, 4.71380473e-02, 4.04040406e-02, 6.73400705e-03,
       1.34680138e-02, 3.36700369e-03, 3.36700336e-10, 3.36700336e-10,
       3.3670

       3.05810394e-10])}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorDirichlet object at 0x00000032F97531D0>}
{'params': {'p': 0.5}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorBeta object at 0x00000032F9753DA0>}
{'params': {'mean': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F9753CC0>}




CATEGORICAL




1 [0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.]
{'params': {'p': array([9.99999987e-01, 3.05810393e-10, 3.05810393e-10, 3.05810393e-10,
       3.05810393e-10, 3.05810393e-10, 3.05810393e-10, 3.05810393e-10,
       3.05810393e-10, 3.05810393e-10, 3.05810393e-10, 3.05810393e-10,
       3.05810393e-10, 3.05810393e-10, 3.05810393e-10, 3.05810393e-10,
       3.05810393e-10, 3.05810393e-10, 3.05810393e-10, 3.05810393e-10,
       3.05810393e-10, 3.05810393e-10, 3.05810393e-10, 3.05810393e-10,
       3.05810393e-10, 3.05810393e-10, 3.05810393e-10, 3.058

 2.08768266e-10 2.08768266e-10 2.08768266e-10 2.08768266e-10])) + 0.3333333333333333*(Geometric(V40|p=0.5)) + 0.3333333333333333*(Poisson(V40|mean=2))) * TypeMixtureUnconstrained(DISCRETE, 0.3333333333333333*(Categorical(V41|p=[0.43215031 0.56784969])) + 0.3333333333333333*(Geometric(V41|p=0.5)) + 0.3333333333333333*(Poisson(V41|mean=2))))))
[0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41]
Done iteration 1/10 in 0.3925706909415112


------------------
Done iteration 2/10 in 0.301267166954176


------------------
Done iteration 3/10 in 0.3060622688208241


------------------
Done iteration 4/10 in 0.29372258912599136


------------------
Done iteration 5/10 in 0.3075429988036831


------------------
Done iteration 6/10 in 0.2984032117353763


------------------
Done iteration 7/10 in 0.2986463814684157


------------------
Done iteration 8/10 in 0.2962581073027195


------------

In [54]:
print("Accuracy of the inferred statistical types is {}".format(accuracy))
print("Accuracy of the inferred statistical types after 5 iterations is {}".format(accuracy_5))
print("Accuracy of the inferred statistical types after 10 iterations is {}".format(accuracy_10))

Accuracy of the inferred statistical types is 0.5952380952380952
Accuracy of the inferred statistical types after 5 iterations is 0.2857142857142857
Accuracy of the inferred statistical types after 10 iterations is 0.2619047619047619


In [35]:
# 3
ground_truth = ['Type.CATEGORICAL', 'Type.CATEGORICAL', 'Type.CATEGORICAL', 'Type.CATEGORICAL', 'Type.CATEGORICAL',
                'Type.CATEGORICAL', 'Type.CATEGORICAL', 'Type.CATEGORICAL', 'Type.CATEGORICAL', 'Type.CATEGORICAL',
                'Type.CATEGORICAL', 'Type.CATEGORICAL', 'Type.CATEGORICAL', 'Type.CATEGORICAL', 'Type.CATEGORICAL', 
                'Type.CATEGORICAL', 'Type.CATEGORICAL', 'Type.CATEGORICAL', 'Type.CATEGORICAL', 'Type.CATEGORICAL', 
                'Type.CATEGORICAL', 'Type.CATEGORICAL', 'Type.CATEGORICAL', 'Type.CATEGORICAL', 'Type.CATEGORICAL', 
                'Type.CATEGORICAL', 'Type.CATEGORICAL', 'Type.CATEGORICAL', 'Type.CATEGORICAL', 'Type.CATEGORICAL', 
                'Type.CATEGORICAL', 'Type.CATEGORICAL', 'Type.CATEGORICAL', 'Type.CATEGORICAL', 'Type.CATEGORICAL', 
                'Type.CATEGORICAL', 'Type.CATEGORICAL']

accuracy = evaluate_bayesian(3, ground_truth)
accuracy_5 = evaluate_bayesian(3, ground_truth, 5)
accuracy_10 = evaluate_bayesian(3, ground_truth, 10)

{'X': array([[1., 1., 1., ..., 0., 0., 0.],
       [1., 1., 1., ..., 0., 0., 0.],
       [1., 1., 1., ..., 0., 0., 0.],
       ...,
       [0., 1., 1., ..., 1., 0., 1.],
       [0., 1., 0., ..., 1., 0., 1.],
       [0., 1., 0., ..., 1., 0., 1.]], dtype=float32), 'T': array([4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4,
       4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4]), 'R': array([2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 3, 2, 2, 2, 2, 2, 2, 2,
       2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2])}

Loaded bayesian/data/temp/data.mat
	with shape: (3196, 37)
	meta-types:[4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4]
	maximal discrete cardinality: [2 2 2 2 2 2 2 2 2 2 2 2 2 2 3 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2]
	meta types [<MetaType.DISCRETE: 3> <MetaType.DISCRETE: 3> <MetaType.DISCRETE: 3>
 <MetaType.DISCRETE: 3> <MetaType.DISCRETE: 3> <MetaType.DISCRETE: 3>
 <MetaType.DISCRETE: 3> <MetaType.DISCRETE: 3> <MetaType.DISCRETE:

1 [0. 0.]
{'params': {'p': array([0.46217105, 0.53782895])}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorDirichlet object at 0x00000032F82A9240>}
{'params': {'p': 0.5}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorBeta object at 0x00000032F82A97B8>}
{'params': {'mean': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F82A9B70>}




CATEGORICAL




1 [0. 0.]
{'params': {'p': array([0.44490132, 0.55509868])}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorDirichlet object at 0x00000032F82A9438>}
{'params': {'p': 0.5}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorBeta object at 0x00000032F82A9A20>}
{'params': {'mean': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F82A9E48>}




CATEGORICAL




1 [0. 0.]
{'params': {'p': array([0.58634868, 0.41365132])}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorDirichlet object at 0x00000032F97317B8>}
{'params': {'p': 0.5}, 'prior': <bayesian.spn.algorithms.Posteri

{'params': {'mean': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F82AF7F0>}




CATEGORICAL




1 [0. 0.]
{'params': {'p': array([0.15131579, 0.84868421])}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorDirichlet object at 0x00000032F82AF898>}
{'params': {'p': 0.5}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorBeta object at 0x00000032F82AF470>}
{'params': {'mean': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F82AF828>}




CATEGORICAL




1 [0. 0.]
{'params': {'p': array([0.05098684, 0.94901316])}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorDirichlet object at 0x00000032F82AF860>}
{'params': {'p': 0.5}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorBeta object at 0x00000032F82AF9E8>}
{'params': {'mean': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F82AFE10>}




CATEGORICAL




1 [0. 0.]
{'params': {'p': array([0.37417763, 0.62582237])}, 'prior': <bayesian.spn.a

{'params': {'p': 0.5}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorBeta object at 0x00000032F974EA58>}
{'params': {'mean': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F974E7B8>}




CATEGORICAL




1 [0. 0.]
{'params': {'p': array([0.04141414, 0.95858586])}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorDirichlet object at 0x00000032F974EB38>}
{'params': {'p': 0.5}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorBeta object at 0x00000032F974ECC0>}
{'params': {'mean': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F974E5C0>}




CATEGORICAL




1 [0. 0.]
{'params': {'p': array([0.65757576, 0.34242424])}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorDirichlet object at 0x00000032F974E1D0>}
{'params': {'p': 0.5}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorBeta object at 0x00000032F974EBE0>}
{'params': {'mean': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F974EBA

{'params': {'p': array([1.00000000e+00, 1.73611111e-10])}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorDirichlet object at 0x00000032F97680F0>}
{'params': {'p': 0.5}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorBeta object at 0x00000032F9768F98>}
{'params': {'mean': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F9768EB8>}




CATEGORICAL




1 [0. 0.]
{'params': {'p': array([1.73611111e-10, 1.00000000e+00])}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorDirichlet object at 0x00000032F9768A58>}
{'params': {'p': 0.5}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorBeta object at 0x00000032F9768CC0>}
{'params': {'mean': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F97686D8>}




CATEGORICAL




1 [0. 0.]
{'params': {'p': array([1.0000e+00, 1.5625e-10])}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorDirichlet object at 0x00000032F9768048>}
{'params': {'p': 0.5}, 'prior': <bayesian.spn.algorithms.P

...

{'params': {'p': array([0.6875, 0.3125])}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorDirichlet object at 0x00000032F82AFFD0>}
{'params': {'p': 0.5}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorBeta object at 0x00000032F82AF828>}
{'params': {'mean': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F82AF470>}




CATEGORICAL




1 [0. 0.]
{'params': {'p': array([0.046875, 0.953125])}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorDirichlet object at 0x00000032F82AFEB8>}
{'params': {'p': 0.5}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorBeta object at 0x00000032F82AF908>}
{'params': {'mean': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F82AF940>}




CATEGORICAL




1 [0. 0.]
{'params': {'p': array([0.00822368, 0.99177632])}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorDirichlet object at 0x00000032F82AF4A8>}
{'params': {'p': 0.5}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorBeta object a


1 [0. 0.]
{'params': {'p': array([0.30454545, 0.69545455])}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorDirichlet object at 0x00000032F6A07320>}
{'params': {'p': 0.5}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorBeta object at 0x00000032F6A076D8>}
{'params': {'mean': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F6A07D30>}




CATEGORICAL




1 [0. 0.]
{'params': {'p': array([0.00707071, 0.99292929])}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorDirichlet object at 0x00000032F97318D0>}
{'params': {'p': 0.5}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorBeta object at 0x00000032F9731C88>}
{'params': {'mean': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F9731908>}




CATEGORICAL




1 [0. 0. 0.]
{'params': {'p': array([0.07272727, 0.7959596 , 0.13131313])}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorDirichlet object at 0x00000032F9731BE0>}
{'params': {'p': 0.5}, 'prior': <bayesian.spn.al

{'params': {'mean': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F9763B38>}




CATEGORICAL




1 [0. 0.]
{'params': {'p': array([0.73636364, 0.26363636])}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorDirichlet object at 0x00000032F9753B70>}
{'params': {'p': 0.5}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorBeta object at 0x00000032F9753BE0>}
{'params': {'mean': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F9753CC0>}




CATEGORICAL




1 [0. 0.]
{'params': {'p': array([0.7489899, 0.2510101])}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorDirichlet object at 0x00000032F97538D0>}
{'params': {'p': 0.5}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorBeta object at 0x00000032F9753550>}
{'params': {'mean': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F9753940>}




CATEGORICAL




1 [0. 0.]
{'params': {'p': array([0.55555556, 0.44444444])}, 'prior': <bayesian.spn.alg

(0.3804755944931164*((TypeMixtureUnconstrained(DISCRETE, 0.3333333333333333*(Categorical(V8|p=[1.00000000e+00 8.22368421e-11])) + 0.3333333333333333*(Geometric(V8|p=0.5)) + 0.3333333333333333*(Poisson(V8|mean=2))) * TypeMixtureUnconstrained(DISCRETE, 0.3333333333333333*(Categorical(V24|p=[8.22368421e-11 1.00000000e+00])) + 0.3333333333333333*(Geometric(V24|p=0.5)) + 0.3333333333333333*(Poisson(V24|mean=2))) * TypeMixtureUnconstrained(DISCRETE, 0.3333333333333333*(Categorical(V27|p=[8.22368421e-11 1.00000000e+00])) + 0.3333333333333333*(Geometric(V27|p=0.5)) + 0.3333333333333333*(Poisson(V27|mean=2))) * TypeMixtureUnconstrained(DISCRETE, 0.3333333333333333*(Categorical(V0|p=[0.13569079 0.86430921])) + 0.3333333333333333*(Geometric(V0|p=0.5)) + 0.3333333333333333*(Poisson(V0|mean=2))) * TypeMixtureUnconstrained(DISCRETE, 0.3333333333333333*(Categorical(V1|p=[0.04440789 0.95559211])) + 0.3333333333333333*(Geometric(V1|p=0.5)) + 0.3333333333333333*(Poisson(V1|mean=2))) * TypeMixtureUnconst

[0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36]
Done iteration 1/10 in 0.46960852041479484


------------------
Done iteration 2/10 in 0.3561098369262936


------------------
Done iteration 3/10 in 0.35248597629095


------------------
Done iteration 4/10 in 0.36310609858639964


------------------
Done iteration 5/10 in 0.3805716857268635


------------------
Done iteration 6/10 in 0.3632474212561192


------------------
Done iteration 7/10 in 0.35388775506180536


------------------
Done iteration 8/10 in 0.3692942945906452


------------------
Done iteration 9/10 in 0.39690353346156826


------------------
Done iteration 10/10 in 0.37488956699212395


------------------
Done in 3.801731005325223
Dumped id to ./exp/temp/data.mat\20181109-144334\global-W.pklz
Dumped id to ./exp/temp/data.mat\20181109-144334\global-type-W.pklz
seeeeeeeeeeeeeeeeeeeeeeeeeee
./exp/temp/data.mat\20181109-144334
['Typ

In [36]:
print("Accuracy of the inferred statistical types is {}".format(accuracy))
print("Accuracy of the inferred statistical types after 5 iterations is {}".format(accuracy_5))
print("Accuracy of the inferred statistical types after 10 iterations is {}".format(accuracy_10))

Accuracy of the inferred statistical types is 0.08108108108108109
Accuracy of the inferred statistical types after 5 iterations is 0.5675675675675675
Accuracy of the inferred statistical types after 10 iterations is 0.7027027027027027


In [59]:
# 1510
ground_truth = ['Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE',
                'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.REAL', 'Type.POSITIVE',
                'Type.REAL', 'Type.REAL', 'Type.REAL', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE',
                'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE',
                'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.REAL', 'Type.POSITIVE',
                'Type.CATEGORICAL']
accuracy = evaluate_bayesian(1510, ground_truth)
accuracy_5 = evaluate_bayesian(1510, ground_truth, 5)
accuracy_10 = evaluate_bayesian(1510, ground_truth, 10)

{'X': array([[1.799e+01, 1.038e+01, 1.228e+02, ..., 4.601e-01, 1.189e-01,
        1.000e+00],
       [2.057e+01, 1.777e+01, 1.329e+02, ..., 2.750e-01, 8.902e-02,
        1.000e+00],
       [1.969e+01, 2.125e+01, 1.300e+02, ..., 3.613e-01, 8.758e-02,
        1.000e+00],
       ...,
       [1.660e+01, 2.808e+01, 1.083e+02, ..., 2.218e-01, 7.820e-02,
        1.000e+00],
       [2.060e+01, 2.933e+01, 1.401e+02, ..., 4.087e-01, 1.240e-01,
        1.000e+00],
       [7.760e+00, 2.454e+01, 4.792e+01, ..., 2.871e-01, 7.039e-02,
        0.000e+00]], dtype=float32), 'T': array([1, 1, 1, 1, 1, 1, 2, 2, 1, 1, 1, 1, 1, 1, 1, 1, 2, 2, 1, 1, 1, 1,
       1, 1, 1, 1, 2, 2, 1, 1, 4]), 'R': array([1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 2])}

Loaded bayesian/data/temp/data.mat
	with shape: (569, 31)
	meta-types:[1 1 1 1 1 1 2 2 1 1 1 1 1 1 1 1 2 2 1 1 1 1 1 1 1 1 2 2 1 1 4]
	maximal discrete cardinality: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 

{'params': {'alpha': 97.56377531321496, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F666ABA8>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F9753DA0>}
gamma fit params (7.222828593197023, 0, 0.03887362290798865)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F9753E80>}
{'params': {'alpha': 7.222828593197023, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F9753518>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F9753CC0>}
gamma fit params (5.029810552119686, 0, 0.24296149580089463)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F9753BE0>}
{'params': {'alpha': 5.029810552119686, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma obje

{'params': {'alpha': 38.87744865028483, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F801DA20>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F801D1D0>}
gamma fit params (39.19579106026804, 0, 0.0019930281137231793)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F801DD68>}
{'params': {'alpha': 39.19579106026804, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F801D9E8>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F801D7F0>}




CATEGORICAL




1 [0. 0.]
{'params': {'p': array([0.96449704, 0.03550296])}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorDirichlet object at 0x00000032F801D748>}
{'params': {'p': 0.5}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorBeta object at 0x00000032F801D5C0>}
{'params': {'mean': 2}, 'p

gamma fit params (3.854201081940556, 0, 0.011752925612901517)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F6A076D8>}
{'params': {'alpha': 3.854201081940556, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F6A07BA8>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F6A07C50>}
gamma fit params (8.826045086835855, 0, 0.0017646257765708841)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F61E81D0>}
{'params': {'alpha': 8.826045086835855, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F61E8358>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F61E8080>}
gamma fit params (6.450509802794781, 0, 0.0032218179094421575)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <

(0.5940246045694201*((TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V0|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V0|alpha=45.03133463022588;beta=1)) + 0.3333333333333333*(Exponential(V0|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V1|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V1|alpha=21.22271320784946;beta=1)) + 0.3333333333333333*(Exponential(V1|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V2|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V2|alpha=43.44801587434889;beta=1)) + 0.3333333333333333*(Exponential(V2|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V3|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V3|alpha=11.183757726494209;beta=1)) + 0.3333333333333333*(Exponential(V3|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V4|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V4|alpha=48.67534939713482;beta=1)) + 0.3333333333333333*(Exponential(V4|l=2))) * TypeMixtureUnconstrained(RE

...

{'params': {'alpha': 1.1, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F9753DA0>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F9753278>}
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F9753DD8>}
{'params': {'alpha': 1.1, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F97539E8>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F9753CC0>}
gamma fit params (52.011493812383605, 0, 0.003331375625042068)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F9753128>}
{'params': {'alpha': 52.011493812383605, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F97531D0>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Post

{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032FA2F5780>}
{'params': {'alpha': 4.543225509611958, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032FA2F5908>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032FA2F5B70>}
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F6A07198>}
{'params': {'alpha': 1.1, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F6A07518>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F6A072B0>}
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F6A07BA8>}
{'params': {'alpha': 1.1, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x000000

gamma fit params (2.2930314298517684, 0, 30.03970658775936)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F82A9A58>}
{'params': {'alpha': 2.2930314298517684, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F82A9198>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F82A9588>}
gamma fit params (8.567185147850273, 0, 0.0007966085144472883)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F82A9AC8>}
{'params': {'alpha': 8.567185147850273, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F82A9D30>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F82A9320>}
gamma fit params (4.127630081849483, 0, 0.008370359784771915)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <ba

(0.5940246045694201*((TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V0|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V0|alpha=45.03133463022588;beta=1)) + 0.3333333333333333*(Exponential(V0|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V1|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V1|alpha=21.22271320784946;beta=1)) + 0.3333333333333333*(Exponential(V1|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V2|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V2|alpha=43.44801587434889;beta=1)) + 0.3333333333333333*(Exponential(V2|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V3|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V3|alpha=11.183757726494209;beta=1)) + 0.3333333333333333*(Exponential(V3|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V4|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V4|alpha=48.67534939713482;beta=1)) + 0.3333333333333333*(Exponential(V4|l=2))) * TypeMixtureUnconstrained(RE

[0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30]
Done iteration 1/10 in 0.19804437847642475


------------------
Done iteration 2/10 in 0.16437523932108888


------------------
Done iteration 3/10 in 0.14808049865587236


------------------
Done iteration 4/10 in 0.14576643862938


------------------
Done iteration 5/10 in 0.1476770579620279


------------------
Done iteration 6/10 in 0.15024849894007275


------------------
Done iteration 7/10 in 0.14837024960434064


------------------
Done iteration 8/10 in 0.14800431073626896


------------------
Done iteration 9/10 in 0.14942148499358154


------------------
Done iteration 10/10 in 0.14743980956973246


------------------
Done in 1.5690120440076498
Dumped id to ./exp/temp/data.mat\20181109-150316\global-W.pklz
Dumped id to ./exp/temp/data.mat\20181109-150316\global-type-W.pklz
seeeeeeeeeeeeeeeeeeeeeeeeeee
./exp/temp/data.mat\20181109-150316
['Type.POSITIVE', 'Type.P

In [60]:
print("Accuracy of the inferred statistical types is {}".format(accuracy))
print("Accuracy of the inferred statistical types after 5 iterations is {}".format(accuracy_5))
print("Accuracy of the inferred statistical types after 10 iterations is {}".format(accuracy_10))

Accuracy of the inferred statistical types is 0.8387096774193549
Accuracy of the inferred statistical types after 5 iterations is 0.8064516129032258
Accuracy of the inferred statistical types after 10 iterations is 0.8387096774193549


In [61]:
# 1489
ground_truth = ['Type.REAL', 'Type.REAL', 'Type.REAL', 'Type.REAL', 'Type.REAL',
                'Type.CATEGORICAL']
accuracy = evaluate_bayesian(1489, ground_truth)
accuracy_5 = evaluate_bayesian(1489, ground_truth, 5)
accuracy_10 = evaluate_bayesian(1489, ground_truth, 10)

{'X': array([[ 0.489927, -0.451528, -1.04799 , -0.598693, -0.020418,  0.      ],
       [-0.641265,  0.109245,  0.29213 , -0.916804,  0.240223,  0.      ],
       [ 0.870593, -0.459862,  0.578159,  0.806634,  0.835248,  0.      ],
       ...,
       [ 0.246882, -0.793228,  1.190101,  1.423194, -1.303036,  1.      ],
       [-0.778907, -0.383111,  1.727029, -1.432389, -1.208085,  0.      ],
       [-0.794604, -0.640053,  0.632221,  0.72028 , -1.231182,  1.      ]],
      dtype=float32), 'T': array([2, 2, 2, 2, 2, 4]), 'R': array([1, 1, 1, 1, 1, 2])}

Loaded bayesian/data/temp/data.mat
	with shape: (5404, 6)
	meta-types:[2 2 2 2 2 4]
	maximal discrete cardinality: [1 1 1 1 1 2]
	meta types [<MetaType.REAL: 1> <MetaType.REAL: 1> <MetaType.REAL: 1>
 <MetaType.REAL: 1> <MetaType.REAL: 1> <MetaType.DISCRETE: 3>]
	domains [array([-2.933743 ,  3.8285749]), array([-3.03870893,  3.66476297]), array([-2.79586911,  2.63086796]), array([-2.48534012,  3.04694796]), array([-2.36746097,  4.58666611]),

(0.5046262028127313*((TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V0|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V0|alpha=1.1;beta=1)) + 0.3333333333333333*(Exponential(V0|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V1|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V1|alpha=1.1;beta=1)) + 0.3333333333333333*(Exponential(V1|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V2|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V2|alpha=1.1;beta=1)) + 0.3333333333333333*(Exponential(V2|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V3|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V3|alpha=1.1;beta=1)) + 0.3333333333333333*(Exponential(V3|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V4|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V4|alpha=1.1;beta=1)) + 0.3333333333333333*(Exponential(V4|l=2))) * TypeMixtureUnconstrained(DISCRETE, 0.3333333333333333*(Categorical(V5|p=[0.49908324 0.50091676])) 

{'params': {'p': array([0.91781845, 0.08218155])}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorDirichlet object at 0x00000032FA2F3390>}
{'params': {'p': 0.5}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorBeta object at 0x00000032FA2F3D30>}
{'params': {'mean': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032FA2F3A58>}
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032FA2F3E48>}
{'params': {'alpha': 1.1, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032FA2F3240>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032FA2F36D8>}
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F666AA90>}
{'params': {'alpha': 1.1, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F666A4E0>}
{'params

MT MetaType.DISCRETE OrderedDict([(<Type.CATEGORICAL: (4, <MetaType.DISCRETE: 3>)>, {<class 'bayesian.spn.structure.leaves.parametric.Parametric.Categorical'>: {'params': {'p': None}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorDirichlet object at 0x00000032F5C98860>}}), (<Type.COUNT: (6, <MetaType.DISCRETE: 3>)>, OrderedDict([(<class 'bayesian.spn.structure.leaves.parametric.Parametric.Geometric'>, {'params': {'p': 0.5}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorBeta object at 0x00000032F7FF3240>}), (<class 'bayesian.spn.structure.leaves.parametric.Parametric.Poisson'>, {'params': {'mean': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F7B20A90>})]))])
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032FB9C7908>}
{'params': {'alpha': 1.1, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032FBA616D8>}
{'params': {'l': 2}, 'prior': 

(0.5046262028127313*((TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V0|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V0|alpha=1.1;beta=1)) + 0.3333333333333333*(Exponential(V0|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V1|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V1|alpha=1.1;beta=1)) + 0.3333333333333333*(Exponential(V1|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V2|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V2|alpha=1.1;beta=1)) + 0.3333333333333333*(Exponential(V2|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V3|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V3|alpha=1.1;beta=1)) + 0.3333333333333333*(Exponential(V3|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V4|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V4|alpha=1.1;beta=1)) + 0.3333333333333333*(Exponential(V4|l=2))) * TypeMixtureUnconstrained(DISCRETE, 0.3333333333333333*(Categorical(V5|p=[0.49908324 0.50091676])) 

In [62]:
print("Accuracy of the inferred statistical types is {}".format(accuracy))
print("Accuracy of the inferred statistical types after 5 iterations is {}".format(accuracy_5))
print("Accuracy of the inferred statistical types after 10 iterations is {}".format(accuracy_10))

Accuracy of the inferred statistical types is 0.5
Accuracy of the inferred statistical types after 5 iterations is 1.0
Accuracy of the inferred statistical types after 10 iterations is 1.0


In [63]:
# 37
ground_truth = ['Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 
                'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.CATEGORICAL']
accuracy = evaluate_bayesian(37, ground_truth)
accuracy_5 = evaluate_bayesian(37, ground_truth, 5)
accuracy_10 = evaluate_bayesian(37, ground_truth, 10)

{'X': array([[  6.   , 148.   ,  72.   , ...,   0.627,  50.   ,   1.   ],
       [  1.   ,  85.   ,  66.   , ...,   0.351,  31.   ,   0.   ],
       [  8.   , 183.   ,  64.   , ...,   0.672,  32.   ,   1.   ],
       ...,
       [  5.   , 121.   ,  72.   , ...,   0.245,  30.   ,   0.   ],
       [  1.   , 126.   ,  60.   , ...,   0.349,  47.   ,   1.   ],
       [  1.   ,  93.   ,  70.   , ...,   0.315,  23.   ,   0.   ]],
      dtype=float32), 'T': array([2, 2, 2, 2, 2, 2, 1, 1, 4]), 'R': array([1, 1, 1, 1, 1, 1, 1, 1, 2])}

Loaded bayesian/data/temp/data.mat
	with shape: (768, 9)
	meta-types:[2 2 2 2 2 2 1 1 4]
	maximal discrete cardinality: [1 1 1 1 1 1 1 1 2]
	meta types [<MetaType.REAL: 1> <MetaType.REAL: 1> <MetaType.REAL: 1>
 <MetaType.REAL: 1> <MetaType.REAL: 1> <MetaType.REAL: 1>
 <MetaType.REAL: 1> <MetaType.REAL: 1> <MetaType.DISCRETE: 3>]
	domains [array([ 0., 17.]), array([  0., 199.]), array([  0., 122.]), array([ 0., 99.]), array([  0., 846.]), array([ 0.        , 67.099

{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032FA2F3390>}
gamma fit params (2.5109224726262864, 0, 0.20267432243967715)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032FA2F3F98>}
{'params': {'alpha': 2.5109224726262864, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032FA2F3BE0>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032FA2F3D68>}
gamma fit params (12.676820593720754, 0, 3.159232183792262)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032FA2F3320>}
{'params': {'alpha': 12.676820593720754, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032FA2F3470>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F7CBC898>}




{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032FA2F39E8>}
{'params': {'alpha': 1.1, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032FA2F3BA8>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032FA2F3438>}
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032FA2F3CF8>}
{'params': {'alpha': 1.1, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032FA2F3908>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032FA2F3DD8>}
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032FA2F3588>}
{'params': {'alpha': 1.1, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F666A4E0>}
{

(0.46875*((TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V0|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V0|alpha=1.1;beta=1)) + 0.3333333333333333*(Exponential(V0|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V1|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V1|alpha=1.1;beta=1)) + 0.3333333333333333*(Exponential(V1|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V2|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V2|alpha=1.1;beta=1)) + 0.3333333333333333*(Exponential(V2|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V3|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V3|alpha=1.1;beta=1)) + 0.3333333333333333*(Exponential(V3|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V4|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V4|alpha=1.1;beta=1)) + 0.3333333333333333*(Exponential(V4|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V5|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V

{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F7CBC208>}
{'params': {'alpha': 1.1, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F7CBC588>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F7CBC4E0>}
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F7CBC550>}
{'params': {'alpha': 1.1, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032FA2F3D30>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032FA2F3A90>}
gamma fit params (2.684103939262438, 0, 0.16017139314463025)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032FA2F3080>}
{'params': {'alpha': 2.684103939262438, 'beta': 1}, 'prior': <bay

(0.46875*((TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V0|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V0|alpha=1.1;beta=1)) + 0.3333333333333333*(Exponential(V0|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V1|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V1|alpha=1.1;beta=1)) + 0.3333333333333333*(Exponential(V1|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V2|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V2|alpha=1.1;beta=1)) + 0.3333333333333333*(Exponential(V2|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V3|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V3|alpha=1.1;beta=1)) + 0.3333333333333333*(Exponential(V3|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V4|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V4|alpha=1.1;beta=1)) + 0.3333333333333333*(Exponential(V4|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V5|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V

In [64]:
print("Accuracy of the inferred statistical types is {}".format(accuracy))
print("Accuracy of the inferred statistical types after 5 iterations is {}".format(accuracy_5))
print("Accuracy of the inferred statistical types after 10 iterations is {}".format(accuracy_10))

Accuracy of the inferred statistical types is 1.0
Accuracy of the inferred statistical types after 5 iterations is 1.0
Accuracy of the inferred statistical types after 10 iterations is 1.0


In [68]:
# 1479
ground_truth = []
for i in range(100):
    ground_truth.append('Type.POSITIVE')
ground_truth.append('Type.CATEGORICAL')
accuracy = evaluate_bayesian(1479, ground_truth)
accuracy_5 = evaluate_bayesian(1479, ground_truth, 5)
accuracy_10 = evaluate_bayesian(1479, ground_truth, 10)

{'X': array([[3.902000e+01, 3.649000e+01, 3.820000e+01, ..., 3.750000e+01,
        3.910000e+01, 0.000000e+00],
       [1.830000e+00, 1.710000e+00, 1.770000e+00, ..., 1.750000e+00,
        1.690000e+00, 1.000000e+00],
       [6.817769e+04, 6.613842e+04, 7.298188e+04, ..., 6.740427e+04,
        7.492024e+04, 1.000000e+00],
       ...,
       [1.016065e+04, 9.048630e+03, 8.994940e+03, ..., 8.997600e+03,
        9.305770e+03, 1.000000e+00],
       [3.481000e+01, 3.507000e+01, 3.498000e+01, ..., 3.283000e+01,
        3.482000e+01, 1.000000e+00],
       [8.489430e+03, 7.672980e+03, 9.132140e+03, ..., 8.389310e+03,
        8.712800e+03, 0.000000e+00]], dtype=float32), 'T': array([1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1

MT MetaType.REAL OrderedDict([(<Type.REAL: (1, <MetaType.REAL: 1>)>, OrderedDict([(<class 'bayesian.spn.structure.leaves.parametric.Parametric.Gaussian'>, {'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032EF231160>})])), (<Type.POSITIVE: (3, <MetaType.REAL: 1>)>, OrderedDict([(<class 'bayesian.spn.structure.leaves.parametric.Parametric.Gamma'>, {'params': {'alpha': None, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032EF231550>}), (<class 'bayesian.spn.structure.leaves.parametric.Parametric.Exponential'>, {'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F27B6128>})]))])
MT MetaType.DISCRETE OrderedDict([(<Type.CATEGORICAL: (4, <MetaType.DISCRETE: 3>)>, {<class 'bayesian.spn.structure.leaves.parametric.Parametric.Categorical'>: {'params': {'p': None}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorDirichlet object at 0x0000

D:\Programfiles\Anaconda3\lib\site-packages\sklearn\cross_decomposition\pls_.py:79: ConvergenceWarning: Maximum number of iterations reached
  ConvergenceWarning)
D:\Programfiles\Anaconda3\lib\site-packages\sklearn\cross_decomposition\pls_.py:79: ConvergenceWarning: Maximum number of iterations reached
  ConvergenceWarning)
D:\Programfiles\Anaconda3\lib\site-packages\sklearn\cross_decomposition\pls_.py:79: ConvergenceWarning: Maximum number of iterations reached
  ConvergenceWarning)
D:\Programfiles\Anaconda3\lib\site-packages\sklearn\cross_decomposition\pls_.py:79: ConvergenceWarning: Maximum number of iterations reached
  ConvergenceWarning)
D:\Programfiles\Anaconda3\lib\site-packages\sklearn\cross_decomposition\pls_.py:79: ConvergenceWarning: Maximum number of iterations reached
  ConvergenceWarning)
D:\Programfiles\Anaconda3\lib\site-packages\sklearn\cross_decomposition\pls_.py:79: ConvergenceWarning: Maximum number of iterations reached
  ConvergenceWarning)
D:\Programfiles\Anacon

D:\Programfiles\Anaconda3\lib\site-packages\sklearn\cross_decomposition\pls_.py:79: ConvergenceWarning: Maximum number of iterations reached
  ConvergenceWarning)
D:\Programfiles\Anaconda3\lib\site-packages\sklearn\cross_decomposition\pls_.py:79: ConvergenceWarning: Maximum number of iterations reached
  ConvergenceWarning)
D:\Programfiles\Anaconda3\lib\site-packages\sklearn\cross_decomposition\pls_.py:79: ConvergenceWarning: Maximum number of iterations reached
  ConvergenceWarning)
D:\Programfiles\Anaconda3\lib\site-packages\sklearn\cross_decomposition\pls_.py:79: ConvergenceWarning: Maximum number of iterations reached
  ConvergenceWarning)
D:\Programfiles\Anaconda3\lib\site-packages\sklearn\cross_decomposition\pls_.py:79: ConvergenceWarning: Maximum number of iterations reached
  ConvergenceWarning)
D:\Programfiles\Anaconda3\lib\site-packages\sklearn\cross_decomposition\pls_.py:79: ConvergenceWarning: Maximum number of iterations reached
  ConvergenceWarning)
D:\Programfiles\Anacon

D:\Programfiles\Anaconda3\lib\site-packages\sklearn\cross_decomposition\pls_.py:79: ConvergenceWarning: Maximum number of iterations reached
  ConvergenceWarning)
D:\Programfiles\Anaconda3\lib\site-packages\sklearn\cross_decomposition\pls_.py:79: ConvergenceWarning: Maximum number of iterations reached
  ConvergenceWarning)
D:\Programfiles\Anaconda3\lib\site-packages\sklearn\cross_decomposition\pls_.py:79: ConvergenceWarning: Maximum number of iterations reached
  ConvergenceWarning)
D:\Programfiles\Anaconda3\lib\site-packages\sklearn\cross_decomposition\pls_.py:79: ConvergenceWarning: Maximum number of iterations reached
  ConvergenceWarning)
D:\Programfiles\Anaconda3\lib\site-packages\sklearn\cross_decomposition\pls_.py:79: ConvergenceWarning: Maximum number of iterations reached
  ConvergenceWarning)
D:\Programfiles\Anaconda3\lib\site-packages\sklearn\cross_decomposition\pls_.py:79: ConvergenceWarning: Maximum number of iterations reached
  ConvergenceWarning)
D:\Programfiles\Anacon

...

{'params': {'alpha': 1.7917450699943174, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032FB9C7BE0>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032FB9C7B00>}
gamma fit params (1.7806787234431918, 0, 58.509740076549804)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032FB9C70B8>}
{'params': {'alpha': 1.7806787234431918, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032FB9C7390>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032FB9C7DA0>}
gamma fit params (1.8087179444833978, 0, 57.68304631811555)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032FB9C7E10>}
{'params': {'alpha': 1.8087179444833978, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma ob

{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032FBA65CF8>}
gamma fit params (1.7776011109010725, 0, 58.92994406822095)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F7EECE80>}
{'params': {'alpha': 1.7776011109010725, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F7EECF98>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F7EEC208>}
gamma fit params (1.7646087863499302, 0, 59.71978961279681)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F7EEC4A8>}
{'params': {'alpha': 1.7646087863499302, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F7EECE10>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F7EECF28>}
gamm

{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032FB9B6710>}
{'params': {'alpha': 1.762958122630515, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032FB9B6898>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032FB9B6DA0>}
gamma fit params (1.7776716177560679, 0, 58.647022644643336)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032FB9B6400>}
{'params': {'alpha': 1.7776716177560679, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032FB9B6550>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F6931390>}
gamma fit params (1.804586229637459, 0, 57.63433705304342)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object a

(0.5*(((0.5066006600660066*((TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V0|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V0|alpha=1.6545988685199116;beta=1)) + 0.3333333333333333*(Exponential(V0|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V1|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V1|alpha=1.6570433180904642;beta=1)) + 0.3333333333333333*(Exponential(V1|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V2|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V2|alpha=1.6414960718966134;beta=1)) + 0.3333333333333333*(Exponential(V2|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V3|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V3|alpha=1.656301074955083;beta=1)) + 0.3333333333333333*(Exponential(V3|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V4|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V4|alpha=1.6658529706781784;beta=1)) + 0.3333333333333333*(Exponential(V4|l=2))) * TypeMixtureUncons

[0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 72, 73, 74, 75, 76, 77, 78, 79, 80, 81, 82, 83, 84, 85, 86, 87, 88, 89, 90, 91, 92, 93, 94, 95, 96, 97, 98, 99, 100]
Done iteration 1/10 in 1.3436094915145986


------------------
Done iteration 2/10 in 1.1959837518406857


------------------
Done iteration 3/10 in 1.252865336864943


------------------
Done iteration 4/10 in 1.2115916169600496


------------------
Done iteration 5/10 in 1.2191121146688602


------------------
Done iteration 6/10 in 1.2030427797139964


------------------
Done iteration 7/10 in 1.2550645228780013


------------------
Done iteration 8/10 in 1.1871120041369068


------------------
Done iteration 9/10 in 1.1669758922475921


------------------
Done iteration 10/10 in 1.200192640957

In [69]:
print("Accuracy of the inferred statistical types is {}".format(accuracy))
print("Accuracy of the inferred statistical types after 5 iterations is {}".format(accuracy_5))
print("Accuracy of the inferred statistical types after 10 iterations is {}".format(accuracy_10))

Accuracy of the inferred statistical types is 0.9900990099009901
Accuracy of the inferred statistical types after 5 iterations is 0.9900990099009901
Accuracy of the inferred statistical types after 10 iterations is 0.9900990099009901


In [70]:
# 1487
ground_truth = []
for i in range(73):
    ground_truth.append('Type.POSITIVE')
for i in [54, 55, 60, 62, 65, 70]:
    ground_truth[i] = 'Type.REAL'
ground_truth[72] = ('Type.CATEGORICAL')
accuracy = evaluate_bayesian(1487, ground_truth)
accuracy_5 = evaluate_bayesian(1487, ground_truth, 5)
accuracy_10 = evaluate_bayesian(1487, ground_truth, 10)

{'X': array([[ 8.0e-01,  1.8e+00,  2.4e+00, ..., -5.5e+01,  0.0e+00,  0.0e+00],
       [ 2.8e+00,  3.2e+00,  3.3e+00, ..., -5.5e+01,  0.0e+00,  0.0e+00],
       [ 2.9e+00,  2.8e+00,  2.6e+00, ..., -4.0e+01,  0.0e+00,  0.0e+00],
       ...,
       [ 8.0e-01,  8.0e-01,  1.2e+00, ..., -3.5e+01,  0.0e+00,  0.0e+00],
       [ 1.3e+00,  9.0e-01,  1.5e+00, ..., -3.0e+01,  5.0e-02,  0.0e+00],
       [ 1.5e+00,  1.3e+00,  1.8e+00, ..., -2.5e+01,  0.0e+00,  0.0e+00]],
      dtype=float32), 'T': array([2, 2, 2, 2, 2, 2, 2, 2, 1, 1, 2, 1, 2, 2, 1, 2, 1, 1, 2, 2, 2, 2,
       2, 2, 1, 1, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 1, 1, 1, 1, 1, 2,
       2, 1, 1, 2, 2, 2, 1, 1, 2, 1, 2, 2, 1, 2, 1, 2, 2, 1, 2, 1, 2, 2,
       1, 2, 2, 1, 2, 2, 4]), 'R': array([1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 2])}

Loaded

D:\Programfiles\Anaconda3\lib\site-packages\sklearn\cross_decomposition\pls_.py:79: ConvergenceWarning: Maximum number of iterations reached
  ConvergenceWarning)
D:\Programfiles\Anaconda3\lib\site-packages\sklearn\cross_decomposition\pls_.py:79: ConvergenceWarning: Maximum number of iterations reached
  ConvergenceWarning)
D:\Programfiles\Anaconda3\lib\site-packages\sklearn\cross_decomposition\pls_.py:79: ConvergenceWarning: Maximum number of iterations reached
  ConvergenceWarning)
D:\Programfiles\Anaconda3\lib\site-packages\sklearn\cross_decomposition\pls_.py:79: ConvergenceWarning: Maximum number of iterations reached
  ConvergenceWarning)
D:\Programfiles\Anaconda3\lib\site-packages\sklearn\cross_decomposition\pls_.py:79: ConvergenceWarning: Maximum number of iterations reached
  ConvergenceWarning)


gamma fit params (50.05839119949871, 0, 0.3397417746784871)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032FA11A128>}
{'params': {'alpha': 50.05839119949871, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032FA11AE80>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032FA11AA90>}
gamma fit params (7.361342555742532, 0, 0.08857434990986783)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032FA11A588>}
{'params': {'alpha': 7.361342555742532, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032FA11A710>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032FA11A048>}
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object a

D:\Programfiles\Anaconda3\lib\site-packages\sklearn\cross_decomposition\pls_.py:79: ConvergenceWarning: Maximum number of iterations reached
  ConvergenceWarning)


{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F64E2710>}
{'params': {'alpha': 1.1, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F64E27B8>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F64E2588>}
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F64E2748>}
{'params': {'alpha': 1.1, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F64E2E48>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F64E2EF0>}
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F64E2780>}
{'params': {'alpha': 1.1, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F64E26D8>}
{

...

{'params': {'alpha': 10.127027691471808, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F7C07B70>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F7C07828>}
gamma fit params (8.797285758376344, 0, 0.4001756575970042)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F7C07748>}
{'params': {'alpha': 8.797285758376344, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F7C070F0>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F7C076D8>}
gamma fit params (7.583012482724425, 0, 0.45151558924950036)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F7C07A20>}
{'params': {'alpha': 7.583012482724425, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma obje

{'params': {'alpha': 1.1, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F686E390>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F686E358>}
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F686E828>}
{'params': {'alpha': 1.1, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F686E7F0>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F686E550>}
gamma fit params (41.63961768901879, 0, 0.10970991421701294)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F63E1898>}
{'params': {'alpha': 41.63961768901879, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F63E1B38>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteri

gamma fit params (38.81743331892555, 0, 0.11667723868136273)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F7F96C88>}
{'params': {'alpha': 38.81743331892555, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F7F96B00>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F7F963C8>}
gamma fit params (39.19489616524945, 0, 0.11584477724557171)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F7F965F8>}
{'params': {'alpha': 39.19489616524945, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F64BDF98>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F64BD748>}
gamma fit params (38.788858745277444, 0, 0.11375431343063701)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <baye

(0.5122336227308603*(((0.174884437596302*((TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V0|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V0|alpha=7.81770543504482;beta=1)) + 0.3333333333333333*(Exponential(V0|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V1|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V1|alpha=11.732504739267327;beta=1)) + 0.3333333333333333*(Exponential(V1|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V2|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V2|alpha=10.189725606042863;beta=1)) + 0.3333333333333333*(Exponential(V2|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V3|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V3|alpha=10.684349948436978;beta=1)) + 0.3333333333333333*(Exponential(V3|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V4|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V4|alpha=10.730189671567933;beta=1)) + 0.3333333333333333*(Exponential(V4|l=2))) * Type

[0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 72]
Done iteration 1/10 in 2.267904358501255


------------------
Done iteration 2/10 in 1.7196951693699702


------------------
Done iteration 3/10 in 1.7040198009640335


------------------
Done iteration 4/10 in 1.6956774211375887


------------------
Done iteration 5/10 in 1.7215118367603282


------------------
Done iteration 6/10 in 1.9178046825963975


------------------
Done iteration 7/10 in 1.7797857264104096


------------------
Done iteration 8/10 in 1.7926472736176038


------------------
Done iteration 9/10 in 1.804210073385093


------------------
Done iteration 10/10 in 1.9712163618492013


------------------
Done in 18.428278350393157
Dumped id to ./exp/temp/data.mat\20181109-151459\global-W.pkl

In [71]:
print("Accuracy of the inferred statistical types is {}".format(accuracy))
print("Accuracy of the inferred statistical types after 5 iterations is {}".format(accuracy_5))
print("Accuracy of the inferred statistical types after 10 iterations is {}".format(accuracy_10))

Accuracy of the inferred statistical types is 0.9315068493150684
Accuracy of the inferred statistical types after 5 iterations is 0.9315068493150684
Accuracy of the inferred statistical types after 10 iterations is 0.8767123287671232


In [72]:
# 1063
ground_truth = ['Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 
                'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 
                'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 
                'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 
                'Type.POSITIVE', 'Type.CATEGORICAL']
accuracy = evaluate_bayesian(1063, ground_truth)
accuracy_5 = evaluate_bayesian(1063, ground_truth, 5)
accuracy_10 = evaluate_bayesian(1063, ground_truth, 10)

{'X': array([[  1.1,   1.4,   1.4, ...,   1.2,   1.4,   0. ],
       [  1. ,   1. ,   1. , ...,   1. ,   1. ,   1. ],
       [415. ,  59. ,  50. , ..., 467. , 106. ,   1. ],
       ...,
       [  4. ,   1. ,   1. , ...,   1. ,   1. ,   1. ],
       [  4. ,   1. ,   1. , ...,   2. ,   1. ,   1. ],
       [  3. ,   1. ,   1. , ...,   0. ,   1. ,   1. ]], dtype=float32), 'T': array([1, 1, 1, 1, 1, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 4, 1, 2, 1, 2, 1, 4]), 'R': array([ 1,  1,  1,  1,  1,  1,  1,  1,  1,  1,  1,  1,  1,  1,  1, 12,  1,
        1,  1,  1,  1,  2])}

Loaded bayesian/data/temp/data.mat
	with shape: (522, 22)
	meta-types:[1 1 1 1 1 2 2 2 2 2 2 2 2 2 2 4 1 2 1 2 1 4]
	maximal discrete cardinality: [ 1  1  1  1  1  1  1  1  1  1  1  1  1  1  1 12  1  1  1  1  1  2]
	meta types [<MetaType.REAL: 1> <MetaType.REAL: 1> <MetaType.REAL: 1>
 <MetaType.REAL: 1> <MetaType.REAL: 1> <MetaType.REAL: 1>
 <MetaType.REAL: 1> <MetaType.REAL: 1> <MetaType.REAL: 1>
 <MetaType.REAL: 1> <MetaType.REAL: 1>

{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F64E0908>}
{'params': {'alpha': 1.1, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F64E05C0>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F64E0CF8>}
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F64E06D8>}
{'params': {'alpha': 1.1, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F64E0AC8>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F64E0DD8>}
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F64E0208>}
{'params': {'alpha': 1.1, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F64E00B8>}
{

gamma fit params (0.47915161206174856, 0, 85523.99600922647)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F6167C50>}
{'params': {'alpha': 0.47915161206174856, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F6167208>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F6167908>}
gamma fit params (1.032372226696916, 0, 0.38399476790303255)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F6167F60>}
{'params': {'alpha': 1.032372226696916, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F6167978>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F6167F98>}
gamma fit params (0.4612526895107892, 0, 5247.000962016665)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <baye

 4.25531913e-10 4.25531913e-10 4.25531955e-03 4.25531955e-03])) + 0.3333333333333333*(Geometric(V15|p=0.5)) + 0.3333333333333333*(Poisson(V15|mean=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V16|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V16|alpha=10.602515921394968;beta=1)) + 0.3333333333333333*(Exponential(V16|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V17|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V17|alpha=2.515596398219457;beta=1)) + 0.3333333333333333*(Exponential(V17|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V18|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V18|alpha=1.369192707680947;beta=1)) + 0.3333333333333333*(Exponential(V18|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V19|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V19|alpha=1.350406566610991;beta=1)) + 0.3333333333333333*(Exponential(V19|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V20|mean=0;st

{'params': {'alpha': 1.1, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F64E0A90>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F64E0320>}
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F64E01D0>}
{'params': {'alpha': 1.1, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F64E0B38>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F64E0CF8>}
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F64E0F98>}
{'params': {'alpha': 1.1, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F7F96F98>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F7F96240>}
{'params': {'mean': 0, 'stdev

{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F7B74D68>}
{'params': {'alpha': 1.3706636005166501, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F6167320>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F6167400>}
gamma fit params (1.0338556540100732, 0, 1150.4818871842103)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F6167BA8>}
{'params': {'alpha': 1.0338556540100732, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F61670B8>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F6167F98>}
gamma fit params (4.037905305894486, 0, 0.017757258315625104)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma obje

 4.25531913e-10 4.25531913e-10 4.25531955e-03 4.25531955e-03])) + 0.3333333333333333*(Geometric(V15|p=0.5)) + 0.3333333333333333*(Poisson(V15|mean=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V16|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V16|alpha=10.602515921394968;beta=1)) + 0.3333333333333333*(Exponential(V16|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V17|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V17|alpha=2.515596398219457;beta=1)) + 0.3333333333333333*(Exponential(V17|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V18|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V18|alpha=1.369192707680947;beta=1)) + 0.3333333333333333*(Exponential(V18|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V19|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V19|alpha=1.350406566610991;beta=1)) + 0.3333333333333333*(Exponential(V19|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V20|mean=0;st

{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F7F96160>}
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F64E0CF8>}
{'params': {'alpha': 1.1, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F698B438>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F7C158D0>}
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F7F96240>}
{'params': {'alpha': 1.1, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F7F96208>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F7F96C88>}
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F64038D0>}
{'params': {'alpha

{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F9731630>}
gamma fit params (1.3706636005166501, 0, 143.72910701421654)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F9731128>}
{'params': {'alpha': 1.3706636005166501, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F9731978>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F97319E8>}
gamma fit params (1.0338556540100732, 0, 1150.4818871842103)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F97316D8>}
{'params': {'alpha': 1.0338556540100732, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F9731198>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F97315C0>}
ga

 4.25531913e-10 4.25531913e-10 4.25531955e-03 4.25531955e-03])) + 0.3333333333333333*(Geometric(V15|p=0.5)) + 0.3333333333333333*(Poisson(V15|mean=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V16|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V16|alpha=10.602515921394968;beta=1)) + 0.3333333333333333*(Exponential(V16|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V17|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V17|alpha=2.515596398219457;beta=1)) + 0.3333333333333333*(Exponential(V17|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V18|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V18|alpha=1.369192707680947;beta=1)) + 0.3333333333333333*(Exponential(V18|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V19|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V19|alpha=1.350406566610991;beta=1)) + 0.3333333333333333*(Exponential(V19|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V20|mean=0;st

In [73]:
print("Accuracy of the inferred statistical types is {}".format(accuracy))
print("Accuracy of the inferred statistical types after 5 iterations is {}".format(accuracy_5))
print("Accuracy of the inferred statistical types after 10 iterations is {}".format(accuracy_10))

Accuracy of the inferred statistical types is 0.9090909090909091
Accuracy of the inferred statistical types after 5 iterations is 0.9090909090909091
Accuracy of the inferred statistical types after 10 iterations is 0.8636363636363636


In [74]:
# 1471
ground_truth = ['Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 
                'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 
                'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.CATEGORICAL']
accuracy = evaluate_bayesian(1471, ground_truth)
accuracy_5 = evaluate_bayesian(1471, ground_truth, 5)
accuracy_10 = evaluate_bayesian(1471, ground_truth, 10)

{'X': array([[4.32923e+03, 4.00923e+03, 4.28923e+03, ..., 4.63590e+03,
        4.39385e+03, 0.00000e+00],
       [4.32462e+03, 4.00462e+03, 4.29385e+03, ..., 4.63282e+03,
        4.38410e+03, 0.00000e+00],
       [4.32769e+03, 4.00667e+03, 4.29538e+03, ..., 4.62872e+03,
        4.38923e+03, 0.00000e+00],
       ...,
       [4.27744e+03, 3.99077e+03, 4.24667e+03, ..., 4.59179e+03,
        4.33949e+03, 1.00000e+00],
       [4.28462e+03, 3.99179e+03, 4.25128e+03, ..., 4.59641e+03,
        4.35077e+03, 1.00000e+00],
       [4.28769e+03, 3.99744e+03, 4.26000e+03, ..., 4.59795e+03,
        4.35077e+03, 1.00000e+00]], dtype=float32), 'T': array([1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 4]), 'R': array([1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2])}

Loaded bayesian/data/temp/data.mat
	with shape: (14980, 15)
	meta-types:[1 1 1 1 1 1 1 1 1 1 1 1 1 1 4]
	maximal discrete cardinality: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 2]
	meta types [<MetaType.REAL: 1> <MetaType.REAL: 1> <MetaType.REAL: 1>
 <MetaTyp

gamma fit params (49609.52668709937, 0, 0.08444904537435581)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F6A6FCF8>}
{'params': {'alpha': 49609.52668709937, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F6A6FA58>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F6A6FE10>}
gamma fit params (23251.604877801612, 0, 0.18354400776026863)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F62008D0>}
{'params': {'alpha': 23251.604877801612, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F6200DD8>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F6200D30>}




CATEGORICAL




1 [0. 0.]
{'params': {'p': array([0.58530864, 0.41469136])}, 'prior': <bayesian.spn.algori

{'params': {'alpha': 148672.49766605912, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F7E3E358>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F7E3E550>}
gamma fit params (92101.31913718744, 0, 0.046521392761223856)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F7E3E4E0>}
{'params': {'alpha': 92101.31913718744, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F6A029E8>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F61677F0>}
gamma fit params (39549.02588900911, 0, 0.10464314231751574)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F6167F98>}
{'params': {'alpha': 39549.02588900911, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma ob

{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F7C15198>}
gamma fit params (20849.46511594375, 0, 0.22315577163661912)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F61E80F0>}
{'params': {'alpha': 20849.46511594375, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F61E80B8>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F61E8208>}
gamma fit params (18355.8262405481, 0, 0.24032128307725786)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F61E8C18>}
{'params': {'alpha': 18355.8262405481, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F61E8CC0>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F61E8128>}
gamma 

{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F62F5320>}
{'params': {'alpha': 419.607399232851, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F62F5780>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F62F5128>}
gamma fit params (126253.69242283086, 0, 0.033411191760719015)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F6AD72E8>}
{'params': {'alpha': 126253.69242283086, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F6AD7780>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F6AD7160>}
gamma fit params (465577.54694444797, 0, 0.00922386250522783)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma obje

...

{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F62F57F0>}
gamma fit params (30270.030289169943, 0, 0.14001708344096714)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F62F5748>}
{'params': {'alpha': 30270.030289169943, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F62F5BA8>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F62F5240>}
gamma fit params (127870.60577268334, 0, 0.03376179184191726)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F80831D0>}
{'params': {'alpha': 127870.60577268334, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F8083550>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F8083438>}


{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F9731F98>}
{'params': {'alpha': 103328.82756036356, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F9731780>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F97315F8>}
gamma fit params (213576.10273373226, 0, 0.020226104240820702)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F9731BE0>}
{'params': {'alpha': 213576.10273373226, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F9731128>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F9731908>}
gamma fit params (419.607399232851, 0, 10.076554794161584)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma objec

{'params': {'alpha': 32282.144838770408, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F7E3E0B8>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F7E3E0F0>}
gamma fit params (15791.108984571432, 0, 0.27688714893524224)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F7E3E8D0>}
{'params': {'alpha': 15791.108984571432, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F7E3ED30>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F7E3EBE0>}
gamma fit params (69118.49054776171, 0, 0.06124425130715194)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F7E3EE10>}
{'params': {'alpha': 69118.49054776171, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma o

(0.45927903871829107*(((0.2719476744186046*(((0.6002137894174239*(((0.5627782724844167*((TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V0|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V0|alpha=223867.17478848403;beta=1)) + 0.3333333333333333*(Exponential(V0|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V13|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V13|alpha=222339.08954044903;beta=1)) + 0.3333333333333333*(Exponential(V13|l=2))))) + 0.43722172751558325*((TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V0|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V0|alpha=23829.14019707002;beta=1)) + 0.3333333333333333*(Exponential(V0|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V13|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V13|alpha=52528.49717230226;beta=1)) + 0.3333333333333333*(Exponential(V13|l=2)))))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V10|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V10|alp

[0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14]
Done iteration 1/10 in 1.5372685249149072


------------------
Done iteration 2/10 in 1.4647636792842604


------------------
Done iteration 3/10 in 1.4560794407098


------------------
Done iteration 4/10 in 1.4450270605279911


------------------
Done iteration 5/10 in 1.4646120929569406


------------------
Done iteration 6/10 in 1.4813375124840604


------------------
Done iteration 7/10 in 1.614170558303158


------------------
Done iteration 8/10 in 1.4789891086802527


------------------
Done iteration 9/10 in 1.4733594925014586


------------------
Done iteration 10/10 in 1.5299564584065592


------------------
Done in 14.971279128062633
Dumped id to ./exp/temp/data.mat\20181109-151748\global-W.pklz
Dumped id to ./exp/temp/data.mat\20181109-151748\global-type-W.pklz
seeeeeeeeeeeeeeeeeeeeeeeeeee
./exp/temp/data.mat\20181109-151748
['Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIV

In [75]:
print("Accuracy of the inferred statistical types is {}".format(accuracy))
print("Accuracy of the inferred statistical types after 5 iterations is {}".format(accuracy_5))
print("Accuracy of the inferred statistical types after 10 iterations is {}".format(accuracy_10))

Accuracy of the inferred statistical types is 1.0
Accuracy of the inferred statistical types after 5 iterations is 1.0
Accuracy of the inferred statistical types after 10 iterations is 1.0


In [76]:
# 1467
ground_truth = ['Type.CATEGORICAL', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 
                'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 
                'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 
                'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 
                'Type.CATEGORICAL']
accuracy = evaluate_bayesian(1467, ground_truth)
accuracy_5 = evaluate_bayesian(1467, ground_truth, 5)
accuracy_10 = evaluate_bayesian(1467, ground_truth, 10)

{'X': array([[1.00000e+00, 1.00000e+00, 5.02000e+02, ..., 7.96997e-01,
        8.69893e-01, 0.00000e+00],
       [1.00000e+00, 2.00000e+00, 2.49000e+02, ..., 4.38447e-01,
        5.12256e-01, 1.00000e+00],
       [1.00000e+00, 3.00000e+00, 2.02000e+02, ..., 2.85636e-01,
        3.65858e-01, 1.00000e+00],
       ...,
       [3.00000e+00, 1.78000e+02, 5.09000e+02, ..., 4.61632e-01,
        6.52817e-01, 1.00000e+00],
       [3.00000e+00, 1.79000e+02, 4.21000e+02, ..., 2.01469e-01,
        5.36535e-01, 1.00000e+00],
       [3.00000e+00, 1.80000e+02, 1.80000e+01, ..., 7.60344e-01,
        7.62439e-01, 1.00000e+00]], dtype=float32), 'T': array([4, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 4]), 'R': array([4, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2])}

Loaded bayesian/data/temp/data.mat
	with shape: (540, 21)
	meta-types:[4 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 4]
	maximal discrete cardinality: [4 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 2]
	meta types [<MetaTyp

{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F64E05C0>}
{'params': {'alpha': 2.0272453372474493, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F64E01D0>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F64E00B8>}
gamma fit params (24.494136337807813, 0, 0.030562400751064107)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F64E0080>}
{'params': {'alpha': 24.494136337807813, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F64E0A90>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F7C15BE0>}
gamma fit params (1.7118501696010877, 0, 0.2815923199114436)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma obj

{'params': {'alpha': 1.843151971118298, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F801D198>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F801D278>}
gamma fit params (1.6975806756815652, 0, 0.2869372494408129)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F801D6D8>}
{'params': {'alpha': 1.6975806756815652, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F801D630>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F801D438>}
gamma fit params (1.616463489348701, 0, 0.30389925593773454)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F801DB38>}
{'params': {'alpha': 1.616463489348701, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma obj

(0.4981481481481482*((TypeMixtureUnconstrained(DISCRETE, 0.3333333333333333*(Categorical(V0|p=[3.34572491e-01 3.34572491e-01 3.30855018e-01 3.71747211e-10])) + 0.3333333333333333*(Geometric(V0|p=0.5)) + 0.3333333333333333*(Poisson(V0|mean=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V1|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V1|alpha=2.0627746971922356;beta=1)) + 0.3333333333333333*(Exponential(V1|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V2|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V2|alpha=1.7299185802656771;beta=1)) + 0.3333333333333333*(Exponential(V2|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V3|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V3|alpha=1.702845815873681;beta=1)) + 0.3333333333333333*(Exponential(V3|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V4|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V4|alpha=1.700515105893134;beta=1)) + 0.3333333333333333*(Exponential(V4|l

[0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20]
Done iteration 1/1 in 0.14547195060777085


------------------
Done in 0.1525293994573076
Dumped id to ./exp/temp/data.mat\20181109-151956\global-W.pklz
Dumped id to ./exp/temp/data.mat\20181109-151956\global-type-W.pklz
seeeeeeeeeeeeeeeeeeeeeeeeeee
./exp/temp/data.mat\20181109-151956
['Type.COUNT', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.COUNT']
{'X': array([[1.00000e+00, 1.00000e+00, 5.02000e+02, ..., 7.96997e-01,
        8.69893e-01, 0.00000e+00],
       [1.00000e+00, 2.00000e+00, 2.49000e+02, ..., 4.38447e-01,
        5.12256e-01, 1.00000e+00],
       [1.00000e+00, 3.00000e+00, 2.02000e+02, ..., 2.85636e-01,
        3.65858e

...

[0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20]
Done iteration 1/5 in 0.17768246612013172


------------------
Done iteration 2/5 in 0.12125287678509267


------------------
Done iteration 3/5 in 0.1078773571871352


------------------
Done iteration 4/5 in 0.0998622301344767


------------------
Done iteration 5/5 in 0.10041252008295487


------------------
Done in 0.6286561319429893
Dumped id to ./exp/temp/data.mat\20181109-151957\global-W.pklz
Dumped id to ./exp/temp/data.mat\20181109-151957\global-type-W.pklz
seeeeeeeeeeeeeeeeeeeeeeeeeee
./exp/temp/data.mat\20181109-151957
['Type.COUNT', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.COUNT']
{'X': array([[1.00000e+00, 1.00000e+0

gamma fit params (1.914298012964948, 0, 0.2680433672894903)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F66D5C50>}
{'params': {'alpha': 1.914298012964948, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F61E84E0>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F61E84A8>}
gamma fit params (1.9657802318936926, 0, 0.25891739593979823)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F61E8E10>}
{'params': {'alpha': 1.9657802318936926, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F61E86D8>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F61E80B8>}
gamma fit params (2.0272453372474493, 0, 0.24724322554910233)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bay

{'params': {'alpha': 1.6857009208722549, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F9731320>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F9731C18>}
gamma fit params (1.8105474571431408, 0, 0.27844639731132603)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F9731748>}
{'params': {'alpha': 1.8105474571431408, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F97316D8>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F9731F28>}
gamma fit params (1.843151971118298, 0, 0.2675305485588981)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F9731AC8>}
{'params': {'alpha': 1.843151971118298, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma ob

(0.4981481481481482*((TypeMixtureUnconstrained(DISCRETE, 0.3333333333333333*(Categorical(V0|p=[3.34572491e-01 3.34572491e-01 3.30855018e-01 3.71747211e-10])) + 0.3333333333333333*(Geometric(V0|p=0.5)) + 0.3333333333333333*(Poisson(V0|mean=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V1|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V1|alpha=2.0627746971922356;beta=1)) + 0.3333333333333333*(Exponential(V1|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V2|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V2|alpha=1.7299185802656771;beta=1)) + 0.3333333333333333*(Exponential(V2|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V3|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V3|alpha=1.702845815873681;beta=1)) + 0.3333333333333333*(Exponential(V3|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V4|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V4|alpha=1.700515105893134;beta=1)) + 0.3333333333333333*(Exponential(V4|l

[0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20]
Done iteration 1/10 in 0.15717765207000411


------------------
Done iteration 2/10 in 0.11705425132549863


------------------
Done iteration 3/10 in 0.10949704130325699


------------------
Done iteration 4/10 in 0.09992025927567738


------------------
Done iteration 5/10 in 0.09990328476487775


------------------
Done iteration 6/10 in 0.10412204278327408


------------------
Done iteration 7/10 in 0.10270842133104452


------------------
Done iteration 8/10 in 0.10035804374683721


------------------
Done iteration 9/10 in 0.1009324138149168


------------------
Done iteration 10/10 in 0.09861519573996702


------------------
Done in 1.1072698276102528
Dumped id to ./exp/temp/data.mat\20181109-151958\global-W.pklz
Dumped id to ./exp/temp/data.mat\20181109-151958\global-type-W.pklz
seeeeeeeeeeeeeeeeeeeeeeeeeee
./exp/temp/data.mat\20181109-151958
['Type.CATEGORICAL', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.P

In [77]:
print("Accuracy of the inferred statistical types is {}".format(accuracy))
print("Accuracy of the inferred statistical types after 5 iterations is {}".format(accuracy_5))
print("Accuracy of the inferred statistical types after 10 iterations is {}".format(accuracy_10))

Accuracy of the inferred statistical types is 0.9047619047619048
Accuracy of the inferred statistical types after 5 iterations is 0.9047619047619048
Accuracy of the inferred statistical types after 10 iterations is 0.6190476190476191


In [80]:
# 1480
ground_truth = ['Type.POSITIVE', 'Type.CATEGORICAL', 'Type.REAL', 'Type.POSITIVE', 'Type.POSITIVE', 
                'Type.POSITIVE', 'Type.POSITIVE', 'Type.REAL', 'Type.REAL', 'Type.REAL', 
                'Type.CATEGORICAL']
accuracy = evaluate_bayesian(1480, ground_truth)
accuracy_5 = evaluate_bayesian(1480, ground_truth, 5)
accuracy_10 = evaluate_bayesian(1480, ground_truth, 10)

{'X': array([[65.  ,  0.  ,  0.7 , ...,  3.3 ,  0.9 ,  0.  ],
       [62.  ,  1.  , 10.9 , ...,  3.2 ,  0.74,  0.  ],
       [62.  ,  1.  ,  7.3 , ...,  3.3 ,  0.89,  0.  ],
       ...,
       [52.  ,  1.  ,  0.8 , ...,  3.2 ,  1.  ,  0.  ],
       [31.  ,  1.  ,  1.3 , ...,  3.4 ,  1.  ,  0.  ],
       [38.  ,  1.  ,  1.  , ...,  4.4 ,  1.5 ,  1.  ]], dtype=float32), 'T': array([1, 4, 1, 1, 1, 1, 1, 1, 1, 1, 4]), 'R': array([1, 2, 1, 1, 1, 1, 1, 1, 1, 1, 2])}

Loaded bayesian/data/temp/data.mat
	with shape: (583, 11)
	meta-types:[1 4 1 1 1 1 1 1 1 1 4]
	maximal discrete cardinality: [1 2 1 1 1 1 1 1 1 1 2]
	meta types [<MetaType.REAL: 1> <MetaType.DISCRETE: 3> <MetaType.REAL: 1>
 <MetaType.REAL: 1> <MetaType.REAL: 1> <MetaType.REAL: 1>
 <MetaType.REAL: 1> <MetaType.REAL: 1> <MetaType.REAL: 1>
 <MetaType.REAL: 1> <MetaType.DISCRETE: 3>]
	domains [array([ 4., 90.]), array([0, 1], dtype=int64), array([ 0.40000001, 75.        ]), array([ 0.1       , 19.70000076]), array([  63., 2110.]), a

{'params': {'mean': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F64E0AC8>}
gamma fit params (0.947893624336071, 0, 6.704971769895008)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F64E0748>}
{'params': {'alpha': 0.947893624336071, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F64E0128>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F64E0D68>}
gamma fit params (0.814883658414526, 0, 3.706050510397895)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F64E0588>}
{'params': {'alpha': 0.814883658414526, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F64E0FD0>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F64E0DD8>}
gamma

(0.5711835334476844*((TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V0|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V0|alpha=5.572847386934386;beta=1)) + 0.3333333333333333*(Exponential(V0|l=2))) * TypeMixtureUnconstrained(DISCRETE, 0.3333333333333333*(Categorical(V1|p=[0.31231231 0.68768769])) + 0.3333333333333333*(Geometric(V1|p=0.5)) + 0.3333333333333333*(Poisson(V1|mean=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V2|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V2|alpha=4.296540988663734;beta=1)) + 0.3333333333333333*(Exponential(V2|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V3|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V3|alpha=1.6719399856055104;beta=1)) + 0.3333333333333333*(Exponential(V3|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V4|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V4|alpha=6.960885501856301;beta=1)) + 0.3333333333333333*(Exponential(V4|l=2))) * TypeMixtureUnconstrained(REAL, 

{'params': {'mean': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F7CBC358>}
gamma fit params (4.296540988663734, 0, 0.2336539810842837)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F7CBC978>}
{'params': {'alpha': 4.296540988663734, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F7CBC0B8>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F7CBC438>}
gamma fit params (1.6719399856055104, 0, 0.20008764734496956)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F6AD72E8>}
{'params': {'alpha': 1.6719399856055104, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F6AD7E80>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F6AD7A90>}


{'params': {'alpha': 8.822808109699041, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F61E8E10>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F61E84E0>}




CATEGORICAL




1 [0. 0.]
{'params': {'p': array([0.9, 0.1])}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorDirichlet object at 0x00000032F61E8198>}
{'params': {'p': 0.5}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorBeta object at 0x00000032F61E86D8>}
{'params': {'mean': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F61E89E8>}
True True True
True True True
(0.5711835334476844*((TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V0|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V0|alpha=5.572847386934386;beta=1)) + 0.3333333333333333*(Exponential(V0|l=2))) * TypeMixtureUnconstrained(DISCRETE, 0.3333333333333333*(Categorical(V1|p=[0.31231231 0.68768769])) + 0.3333333333333333*(Geometric(V1|

MT MetaType.DISCRETE OrderedDict([(<Type.CATEGORICAL: (4, <MetaType.DISCRETE: 3>)>, {<class 'bayesian.spn.structure.leaves.parametric.Parametric.Categorical'>: {'params': {'p': None}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorDirichlet object at 0x00000032F5C98860>}}), (<Type.COUNT: (6, <MetaType.DISCRETE: 3>)>, OrderedDict([(<class 'bayesian.spn.structure.leaves.parametric.Parametric.Geometric'>, {'params': {'p': 0.5}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorBeta object at 0x00000032F7FF3240>}), (<class 'bayesian.spn.structure.leaves.parametric.Parametric.Poisson'>, {'params': {'mean': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F7B20A90>})]))])
gamma fit params (5.572847386934386, 0, 7.42823076286833)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F6AD7860>}
{'params': {'alpha': 5.572847386934386, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.

{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F61E8240>}
{'params': {'alpha': 0.8401348814764473, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F61E8E10>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F61E80B8>}
gamma fit params (32.47309356540379, 0, 0.18877166681702015)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F61E8898>}
{'params': {'alpha': 32.47309356540379, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F61E84A8>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F61E8A20>}
gamma fit params (15.665583914667975, 0, 0.1682924817668932)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object

In [81]:
print("Accuracy of the inferred statistical types is {}".format(accuracy))
print("Accuracy of the inferred statistical types after 5 iterations is {}".format(accuracy_5))
print("Accuracy of the inferred statistical types after 10 iterations is {}".format(accuracy_10))

Accuracy of the inferred statistical types is 0.5454545454545454
Accuracy of the inferred statistical types after 5 iterations is 0.9090909090909091
Accuracy of the inferred statistical types after 10 iterations is 1.0


In [82]:
# 1068
ground_truth = ['Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 
                'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 
                'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 
                'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 
                'Type.POSITIVE', 'Type.CATEGORICAL']
accuracy = evaluate_bayesian(1068, ground_truth)
accuracy_5 = evaluate_bayesian(1068, ground_truth, 5)
accuracy_10 = evaluate_bayesian(1068, ground_truth, 10)

{'X': array([[  1.1,   1.4,   1.4, ...,   1.2,   1.4,   0. ],
       [  1. ,   1. ,   1. , ...,   1. ,   1. ,   1. ],
       [ 91. ,   9. ,   3. , ..., 126. ,  17. ,   1. ],
       ...,
       [  5. ,   3. ,   3. , ...,   6. ,   5. ,   0. ],
       [ 18. ,   8. ,   5. , ...,  50. ,  15. ,   0. ],
       [ 26. ,  18. ,  13. , ..., 109. ,  35. ,   0. ]], dtype=float32), 'T': array([2, 1, 1, 1, 1, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 1, 2, 1, 2, 1, 4]), 'R': array([1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2])}

Loaded bayesian/data/temp/data.mat
	with shape: (1109, 22)
	meta-types:[2 1 1 1 1 2 2 2 2 2 2 2 2 2 2 2 1 2 1 2 1 4]
	maximal discrete cardinality: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 2]
	meta types [<MetaType.REAL: 1> <MetaType.REAL: 1> <MetaType.REAL: 1>
 <MetaType.REAL: 1> <MetaType.REAL: 1> <MetaType.REAL: 1>
 <MetaType.REAL: 1> <MetaType.REAL: 1> <MetaType.REAL: 1>
 <MetaType.REAL: 1> <MetaType.REAL: 1> <MetaType.REAL: 1>
 <MetaType.REAL: 1> <MetaType.

D:\Programfiles\Anaconda3\lib\site-packages\sklearn\cross_decomposition\pls_.py:79: ConvergenceWarning: Maximum number of iterations reached
  ConvergenceWarning)
D:\Programfiles\Anaconda3\lib\site-packages\sklearn\cross_decomposition\pls_.py:79: ConvergenceWarning: Maximum number of iterations reached
  ConvergenceWarning)


gamma fit params (5.9188847553123916, 0, 0.23112699710603687)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F66D5C18>}
{'params': {'alpha': 5.9188847553123916, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F693FA58>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F693FB00>}
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F7C15BE0>}
{'params': {'alpha': 1.1, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F640E908>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F640EAC8>}




CATEGORICAL




1 [0. 0.]
{'params': {'p': array([0.96660808, 0.03339192])}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorDirichlet object at 0x00000032F640EBA8>}
{'params': {'

{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F97314A8>}
{'params': {'alpha': 1.1, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F9731AC8>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F97318D0>}
gamma fit params (3.901497754357835, 0, 1.3433161344828521)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F9731208>}
{'params': {'alpha': 3.901497754357835, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F97316D8>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F9731240>}
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F9731358>}
{'params': {'alpha': 1.1, 'beta': 1}, 'prior': <baye

{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F7E3E1D0>}
gamma fit params (2402.765407721859, 0, 0.0004167347283165016)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F7E3EBE0>}
{'params': {'alpha': 2402.765407721859, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F7E3EF28>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F7E3EE10>}
gamma fit params (2402.765407721859, 0, 0.0004167347283165016)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F7E3EBA8>}
{'params': {'alpha': 2402.765407721859, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F7E3EA58>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F7E3E470>}


...

{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F7E3E0B8>}
{'params': {'alpha': 1.1, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F7E3E128>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F7E3E668>}
gamma fit params (3.901497754357835, 0, 1.3433161344828521)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F7E3E5F8>}
{'params': {'alpha': 3.901497754357835, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F7E3E588>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F7E3EA20>}
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F7E3E550>}
{'params': {'alpha': 1.1, 'beta': 1}, 'prior': <baye

{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F63F2518>}
gamma fit params (2402.765407721859, 0, 0.0004167347283165016)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F63F2048>}
{'params': {'alpha': 2402.765407721859, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F63F22E8>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F63F2208>}
gamma fit params (2402.765407721859, 0, 0.0004167347283165016)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F7B35710>}
{'params': {'alpha': 2402.765407721859, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F7B35358>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F7B35B38>}


{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F97315F8>}
{'params': {'alpha': 12.335917850215889, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F9731438>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F97317F0>}
gamma fit params (9.852330832268756, 0, 4.082469791988384)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F9731198>}
{'params': {'alpha': 9.852330832268756, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F9731320>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F9731F98>}
gamma fit params (2.699167943185453, 0, 3.1042305506026815)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at

(0.5130748422001803*(((0.44639718804920914*((TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V0|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V0|alpha=1.1;beta=1)) + 0.3333333333333333*(Exponential(V0|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V4|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V4|alpha=1.9928284231137754;beta=1)) + 0.3333333333333333*(Exponential(V4|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V5|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V5|alpha=1.1;beta=1)) + 0.3333333333333333*(Exponential(V5|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V6|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V6|alpha=1.1;beta=1)) + 0.3333333333333333*(Exponential(V6|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V7|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V7|alpha=1.1;beta=1)) + 0.3333333333333333*(Exponential(V7|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(

[0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21]
Done iteration 1/10 in 0.2980688533521061


------------------
Done iteration 2/10 in 0.22439908258684227


------------------
Done iteration 3/10 in 0.2184449769265484


------------------
Done iteration 4/10 in 0.2168991121934596


------------------
Done iteration 5/10 in 0.23056911981257144


------------------
Done iteration 6/10 in 0.23425929946597535


------------------
Done iteration 7/10 in 0.2205940289195496


------------------
Done iteration 8/10 in 0.2195826638926519


------------------
Done iteration 9/10 in 0.22294045894341252


------------------
Done iteration 10/10 in 0.21786981734658184


------------------
Done in 2.3233028450072197
Dumped id to ./exp/temp/data.mat\20181109-152135\global-W.pklz
Dumped id to ./exp/temp/data.mat\20181109-152135\global-type-W.pklz
seeeeeeeeeeeeeeeeeeeeeeeeeee
./exp/temp/data.mat\20181109-152135
['Type.POSITIVE', 'Type.POSITIVE', 'Type.REAL', 'Type.POSITIVE

In [83]:
print("Accuracy of the inferred statistical types is {}".format(accuracy))
print("Accuracy of the inferred statistical types after 5 iterations is {}".format(accuracy_5))
print("Accuracy of the inferred statistical types after 10 iterations is {}".format(accuracy_10))

Accuracy of the inferred statistical types is 1.0
Accuracy of the inferred statistical types after 5 iterations is 0.9545454545454546
Accuracy of the inferred statistical types after 10 iterations is 0.9545454545454546


In [84]:
# 1492
ground_truth = ['Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 
                'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 
                'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 
                'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 
                'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 
                'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 
                'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 
                'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 
                'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 
                'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 
                'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 
                'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 
                'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.CATEGORICAL']

accuracy = evaluate_bayesian(1492, ground_truth)
accuracy_5 = evaluate_bayesian(1492, ground_truth, 5)
accuracy_10 = evaluate_bayesian(1492, ground_truth, 10)

{'X': array([[5.79e-04, 6.09e-04, 5.51e-04, ..., 6.17e-04, 6.14e-04, 1.20e+01],
       [6.30e-04, 6.61e-04, 7.19e-04, ..., 6.71e-04, 6.67e-04, 1.20e+01],
       [6.16e-04, 6.15e-04, 6.06e-04, ..., 6.07e-04, 6.02e-04, 1.20e+01],
       ...,
       [7.01e-04, 6.42e-04, 6.46e-04, ..., 6.22e-04, 6.63e-04, 2.00e+00],
       [7.09e-04, 7.76e-04, 7.16e-04, ..., 6.83e-04, 7.02e-04, 2.00e+00],
       [8.50e-04, 7.70e-04, 7.64e-04, ..., 8.10e-04, 7.97e-04, 2.00e+00]],
      dtype=float32), 'T': array([1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2]), 'R': array([1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1])}

Loaded bayesian/data/temp/data.mat
	with shape: (1600, 65)
	meta-typ

D:\Programfiles\Anaconda3\lib\site-packages\sklearn\cross_decomposition\pls_.py:79: ConvergenceWarning: Maximum number of iterations reached
  ConvergenceWarning)
D:\Programfiles\Anaconda3\lib\site-packages\sklearn\cross_decomposition\pls_.py:79: ConvergenceWarning: Maximum number of iterations reached
  ConvergenceWarning)


{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032FA11A9E8>}
{'params': {'alpha': 1.1, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032FA11A940>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032FA11A2E8>}


D:\Programfiles\Anaconda3\lib\site-packages\sklearn\cross_decomposition\pls_.py:79: ConvergenceWarning: Maximum number of iterations reached
  ConvergenceWarning)
D:\Programfiles\Anaconda3\lib\site-packages\sklearn\cross_decomposition\pls_.py:79: ConvergenceWarning: Maximum number of iterations reached
  ConvergenceWarning)


{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F64E2400>}
{'params': {'alpha': 1.1, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F64E2320>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F64E24E0>}
gamma fit params (12.849018071847684, 0, 3.3961159326277766e-05)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F64E2668>}
{'params': {'alpha': 12.849018071847684, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F64E21D0>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F64E2A20>}
gamma fit params (12.833858922022932, 0, 3.213096235463534e-05)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x0

...

gamma fit params (43.58490522605466, 0, 1.71685740514581e-05)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F7B74D68>}
{'params': {'alpha': 43.58490522605466, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F7B74278>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F679FC18>}
gamma fit params (40.95187465849605, 0, 1.9428391857701196e-05)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F679FCF8>}
{'params': {'alpha': 40.95187465849605, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F679F0F0>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F679F780>}
gamma fit params (40.03240551367586, 0, 2.1108929230193512e-05)
{'params': {'mean': 0, 'stdev': 1}, 'prior':

{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F63E87B8>}
{'params': {'alpha': 34.393381802419846, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F63E8A20>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F63E8550>}
gamma fit params (26.060813696877013, 0, 1.7970398641222116e-05)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F63E8EB8>}
{'params': {'alpha': 26.060813696877013, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F63E82B0>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F63E8358>}
gamma fit params (21.93591314803734, 0, 2.0669261829378848e-05)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamm

{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F62800B8>}
{'params': {'alpha': 29.747838486363104, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F6280C88>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F6280828>}
gamma fit params (28.78419871880063, 0, 3.3725270255702386e-05)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F62807F0>}
{'params': {'alpha': 28.78419871880063, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F62802B0>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F62807B8>}
True True True
True True True


(0.436875*(((0.43204577968526464*((TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V0|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V0|alpha=12.849018071847684;beta=1)) + 0.3333333333333333*(Exponential(V0|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V1|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V1|alpha=12.833858922022932;beta=1)) + 0.3333333333333333*(Exponential(V1|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V2|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V2|alpha=12.540056076017919;beta=1)) + 0.3333333333333333*(Exponential(V2|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V3|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V3|alpha=11.867288992163187;beta=1)) + 0.3333333333333333*(Exponential(V3|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V4|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V4|alpha=11.441125187891954;beta=1)) + 0.3333333333333333*(Exponential(V4|l=2))) * TypeMixtur

[0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 63, 64]
Done iteration 1/10 in 0.9565456476170766


------------------
Done iteration 2/10 in 0.7982405722382282


------------------
Done iteration 3/10 in 0.7859162880299664


------------------
Done iteration 4/10 in 0.7899017452168664


------------------
Done iteration 5/10 in 0.7846037241283739


------------------
Done iteration 6/10 in 0.7872481949775647


------------------
Done iteration 7/10 in 0.7864772363918746


------------------
Done iteration 8/10 in 0.7841844931922424


------------------
Done iteration 9/10 in 0.7812956683414995


------------------
Done iteration 10/10 in 0.7964266681406116


------------------
Done in 8.07710849080786
Dumped id to ./exp/temp/data.mat\20181109-152251\global-W.pklz
Dumped id to ./exp/temp/data.m

In [85]:
print("Accuracy of the inferred statistical types is {}".format(accuracy))
print("Accuracy of the inferred statistical types after 5 iterations is {}".format(accuracy_5))
print("Accuracy of the inferred statistical types after 10 iterations is {}".format(accuracy_10))

Accuracy of the inferred statistical types is 0.9846153846153847
Accuracy of the inferred statistical types after 5 iterations is 0.9846153846153847
Accuracy of the inferred statistical types after 10 iterations is 0.9846153846153847


In [88]:
# 1050
ground_truth = ['Type.POSITIVE', 'Type.COUNT', 'Type.COUNT', 'Type.CATEGORICAL', 'Type.POSITIVE', 
                'Type.COUNT', 'Type.POSITIVE', 'Type.REAL', 'Type.POSITIVE', 'Type.REAL', 
                'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.CATEGORICAL', 'Type.POSITIVE', 
                'Type.POSITIVE', 'Type.COUNT', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 
                'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 'Type.POSITIVE', 
                'Type.POSITIVE', 'Type.COUNT', 'Type.COUNT', 'Type.COUNT', 'Type.POSITIVE', 
                'Type.COUNT', 'Type.COUNT', 'Type.COUNT', 'Type.COUNT', 'Type.COUNT',
                'Type.POSITIVE', 'Type.POSITIVE', 'Type.CATEGORICAL']

accuracy = evaluate_bayesian(1050, ground_truth)
accuracy_5 = evaluate_bayesian(1050, ground_truth, 5)
accuracy_10 = evaluate_bayesian(1050, ground_truth, 10)

{'X': array([[ 2.  ,  1.  ,  0.  , ...,  0.  , 10.  ,  0.  ],
       [ 1.  ,  1.  ,  4.  , ...,  0.  , 14.  ,  0.  ],
       [27.  , 19.  ,  1.  , ..., 30.91, 42.  ,  0.  ],
       ...,
       [ 0.  ,  1.  ,  0.  , ...,  0.  ,  0.  ,  0.  ],
       [ 0.  ,  7.  ,  0.  , ...,  0.  , 11.  ,  0.  ],
       [ 1.  ,  9.  ,  0.  , ...,  0.  , 11.  ,  0.  ]], dtype=float32), 'T': array([2, 1, 4, 4, 2, 2, 1, 1, 2, 2, 1, 1, 1, 4, 2, 2, 4, 2, 2, 2, 2, 1,
       2, 2, 2, 1, 2, 2, 1, 1, 2, 1, 2, 1, 1, 2, 2, 4]), 'R': array([ 1,  1, 25, 43,  1,  1,  1,  1,  1,  1,  1,  1,  1, 71,  1,  1,  8,
        1,  1,  1,  1,  1,  1,  1,  1,  1,  1,  1,  1,  1,  1,  1,  1,  1,
        1,  1,  1,  2])}

Loaded bayesian/data/temp/data.mat
	with shape: (1563, 38)
	meta-types:[2 1 4 4 2 2 1 1 2 2 1 1 1 4 2 2 4 2 2 2 2 1 2 2 2 1 2 2 1 1 2 1 2 1 1 2 2
 4]
	maximal discrete cardinality: [ 1  1 25 43  1  1  1  1  1  1  1  1  1 71  1  1  8  1  1  1  1  1  1  1
  1  1  1  1  1  1  1  1  1  1  1  1  1  2]
	meta types [<M

D:\Programfiles\Anaconda3\lib\site-packages\sklearn\cross_decomposition\pls_.py:79: ConvergenceWarning: Maximum number of iterations reached
  ConvergenceWarning)
D:\Programfiles\Anaconda3\lib\site-packages\sklearn\cross_decomposition\pls_.py:79: ConvergenceWarning: Maximum number of iterations reached
  ConvergenceWarning)






CATEGORICAL




1 [0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0.]
{'params': {'p': array([3.81258022e-01, 3.20924261e-01, 1.55327342e-01, 7.57381257e-02,
       2.82413351e-02, 1.54043646e-02, 1.15532735e-02, 3.85109126e-03,
       2.56739422e-03, 3.85109126e-03, 1.28369717e-03, 1.28369704e-10,
       1.28369704e-10, 1.28369704e-10, 1.28369704e-10, 1.28369704e-10,
       1.28369704e-10, 1.28369704e-10, 1.28369704e-10, 1.28369704e-10,
       1.28369704e-10, 1.28369704e-10, 1.28369704e-10, 1.28369704e-10,
       1.28369704e-10])}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorDirichlet object at 0x00000032F9731470>}
{'params': {'p': 0.5}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorBeta object at 0x00000032F9731320>}
{'params': {'mean': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F97317F0>}




CATEGORICAL




1 [0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 

{'params': {'mean': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F82AFF28>}
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F6749C18>}
{'params': {'alpha': 1.1, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F6749F28>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F6749BA8>}
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F66594A8>}
{'params': {'alpha': 1.1, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F66595F8>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F6659780>}
gamma fit params (3.101436400507435, 0, 0.13911796532583917)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNorm

{'params': {'alpha': 1.1, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F69319E8>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F6931908>}
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F6931EF0>}
{'params': {'alpha': 1.1, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F6931828>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F6931D68>}
gamma fit params (3.1459869462838497, 0, 0.06917072910888865)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F6931198>}
{'params': {'alpha': 3.1459869462838497, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F640EDD8>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Poste

...

{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F82AF710>}
gamma fit params (8.287266953247467, 0, 1.7353750843083617)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F82AF8D0>}
{'params': {'alpha': 8.287266953247467, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F82AF748>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F82AF438>}
gamma fit params (5.369812317045459, 0, 7.157795596568256)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F82AFD68>}
{'params': {'alpha': 5.369812317045459, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F82AFE10>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F82AF7B8>}
gamma f

{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F611BB00>}
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F65B7B00>}
{'params': {'alpha': 1.1, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F65B7978>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F65B7DD8>}
gamma fit params (0.5451401513079825, 0, 13770.383439788746)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F65B70F0>}
{'params': {'alpha': 0.5451401513079825, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F65B7550>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F65B7DA0>}
gamma fit params (1.2004086616644662, 0, 2136.9151396388015)
{'params': {'mean

 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.]
{'params': {'p': array([8.64864851e-01, 2.25225222e-10, 6.75675667e-02, 2.02702702e-02,
       1.80180180e-02, 6.75675687e-03, 2.25225244e-03, 2.25225244e-03,
       2.25225244e-03, 2.25225244e-03, 2.25225244e-03, 2.25225222e-10,
       2.25225244e-03, 2.25225222e-10, 4.50450466e-03, 2.25225222e-10,
       2.25225222e-10, 2.25225244e-03, 2.25225222e-10, 2.25225222e-10,
       2.25225222e-10, 2.25225222e-10, 2.25225222e-10, 2.25225222e-10,
       2.25225222e-10, 2.25225222e-10, 2.25225244e-03, 2.25225222e-10,
       2.25225222e-10, 2.25225222e-10, 2.25225222e-10, 2.25225222e-10,
       2.25225222e-10, 2.25225222e-10, 2.25225222e-10, 2.25225222e-10,
       2.25225222e-10, 2.25225222e-10, 2.25225222e-10, 2.25225222e-10,
       2.25225222e-10, 2.25225222e-10, 2.25225222e-10, 2.25225222e-10,
       2.25225222e-10, 2.25225222e-10, 2.25225222e-10, 2.25225222e-10,
       2.25225222e-10, 2.25225222e-10, 2.25225222e-10, 2.252

{'params': {'alpha': 1.1, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F801DF28>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F801D080>}
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F801DFD0>}
{'params': {'alpha': 1.1, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F67496A0>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F6749F98>}
gamma fit params (4.2630674694405375, 0, 0.8071386916048394)
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F6749208>}
{'params': {'alpha': 4.2630674694405375, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F67499B0>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Poster

 0.00255102 0.00255102])) + 0.3333333333333333*(Geometric(V16|p=0.5)) + 0.3333333333333333*(Poisson(V16|mean=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V33|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V33|alpha=9.902003983851777;beta=1)) + 0.3333333333333333*(Exponential(V33|l=2))) * TypeMixtureUnconstrained(DISCRETE, 0.3333333333333333*(Categorical(V37|p=[0.82397959 0.17602041])) + 0.3333333333333333*(Geometric(V37|p=0.5)) + 0.3333333333333333*(Poisson(V37|mean=2))))))
[0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37]
Done iteration 1/10 in 0.5510419586216813


------------------
Done iteration 2/10 in 0.4441467545134401


------------------
Done iteration 3/10 in 0.4442407064557301


------------------
Done iteration 4/10 in 0.44713624215910386


------------------
Done iteration 5/10 in 0.4509744553351993


------------------
Done iteration 6/10 in 0.4447045448264362


In [89]:
print("Accuracy of the inferred statistical types is {}".format(accuracy))
print("Accuracy of the inferred statistical types after 5 iterations is {}".format(accuracy_5))
print("Accuracy of the inferred statistical types after 10 iterations is {}".format(accuracy_10))

Accuracy of the inferred statistical types is 0.6842105263157895
Accuracy of the inferred statistical types after 5 iterations is 0.6842105263157895
Accuracy of the inferred statistical types after 10 iterations is 0.7105263157894737


In [92]:
# 1462
ground_truth = ['Type.REAL', 'Type.POSITIVE', 'Type.REAL', 'Type.REAL', 'Type.CATEGORICAL']
accuracy = evaluate_bayesian(1462, ground_truth)
accuracy_5 = evaluate_bayesian(1462, ground_truth, 5)
accuracy_10 = evaluate_bayesian(1462, ground_truth, 10)

{'X': array([[  3.6216 ,   8.6661 ,  -2.8073 ,  -0.44699,   0.     ],
       [  4.5459 ,   8.1674 ,  -2.4586 ,  -1.4621 ,   0.     ],
       [  3.866  ,  -2.6383 ,   1.9242 ,   0.10645,   0.     ],
       ...,
       [ -3.7503 , -13.4586 ,  17.5932 ,  -2.7771 ,   1.     ],
       [ -3.5637 ,  -8.3827 ,  12.393  ,  -1.2823 ,   1.     ],
       [ -2.5419 ,  -0.65804,   2.6842 ,   1.1952 ,   1.     ]],
      dtype=float32), 'T': array([2, 2, 2, 2, 4]), 'R': array([1, 1, 1, 1, 2])}

Loaded bayesian/data/temp/data.mat
	with shape: (1372, 5)
	meta-types:[2 2 2 2 4]
	maximal discrete cardinality: [1 1 1 1 2]
	meta types [<MetaType.REAL: 1> <MetaType.REAL: 1> <MetaType.REAL: 1>
 <MetaType.REAL: 1> <MetaType.DISCRETE: 3>]
	domains [array([-7.04209995,  6.82480001]), array([-13.7730999 ,  12.95160007]), array([-5.28609991, 17.92740059]), array([-8.54819965,  2.44950008]), array([0, 1], dtype=int64)]
	translated discrete features (starting from 0)
MT MetaType.REAL OrderedDict([(<Type.REAL: (1, <M

(0.48177842565597667*((TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V0|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V0|alpha=1.1;beta=1)) + 0.3333333333333333*(Exponential(V0|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V1|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V1|alpha=3.977255468506035;beta=1)) + 0.3333333333333333*(Exponential(V1|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V2|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V2|alpha=1.1;beta=1)) + 0.3333333333333333*(Exponential(V2|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V3|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V3|alpha=1.1;beta=1)) + 0.3333333333333333*(Exponential(V3|l=2))) * TypeMixtureUnconstrained(DISCRETE, 0.3333333333333333*(Categorical(V4|p=[0.62481089 0.37518911])) + 0.3333333333333333*(Geometric(V4|p=0.5)) + 0.3333333333333333*(Poisson(V4|mean=2))))) + 0.5182215743440233*(((0.5246132208157525*((TypeMixtureUnconstrained(REA

{'params': {'p': array([0.03485255, 0.96514745])}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorDirichlet object at 0x00000032F80A5630>}
{'params': {'p': 0.5}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorBeta object at 0x00000032F6ACEEF0>}
{'params': {'mean': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F6ACE518>}
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F6ACE860>}
{'params': {'alpha': 1.1, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F6ACE080>}
{'params': {'l': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F63F2198>}




CATEGORICAL




1 [0. 0.]
{'params': {'p': array([0.99408284, 0.00591716])}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorDirichlet object at 0x00000032F63F2048>}
{'params': {'p': 0.5}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorBeta object at 0x0000003

MT MetaType.DISCRETE OrderedDict([(<Type.CATEGORICAL: (4, <MetaType.DISCRETE: 3>)>, {<class 'bayesian.spn.structure.leaves.parametric.Parametric.Categorical'>: {'params': {'p': None}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorDirichlet object at 0x00000032F5C98860>}}), (<Type.COUNT: (6, <MetaType.DISCRETE: 3>)>, OrderedDict([(<class 'bayesian.spn.structure.leaves.parametric.Parametric.Geometric'>, {'params': {'p': 0.5}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorBeta object at 0x00000032F7FF3240>}), (<class 'bayesian.spn.structure.leaves.parametric.Parametric.Poisson'>, {'params': {'mean': 2}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F7B20A90>})]))])
{'params': {'mean': 0, 'stdev': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorNormalInverseGamma object at 0x00000032F6ACE240>}
{'params': {'alpha': 1.1, 'beta': 1}, 'prior': <bayesian.spn.algorithms.Posteriors.PriorGamma object at 0x00000032F6ACE1D0>}
{'params': {'l': 2}, 'prior': 

(0.48177842565597667*((TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V0|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V0|alpha=1.1;beta=1)) + 0.3333333333333333*(Exponential(V0|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V1|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V1|alpha=3.977255468506035;beta=1)) + 0.3333333333333333*(Exponential(V1|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V2|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V2|alpha=1.1;beta=1)) + 0.3333333333333333*(Exponential(V2|l=2))) * TypeMixtureUnconstrained(REAL, 0.3333333333333333*(Gaussian(V3|mean=0;stdev=1)) + 0.3333333333333333*(Gamma(V3|alpha=1.1;beta=1)) + 0.3333333333333333*(Exponential(V3|l=2))) * TypeMixtureUnconstrained(DISCRETE, 0.3333333333333333*(Categorical(V4|p=[0.62481089 0.37518911])) + 0.3333333333333333*(Geometric(V4|p=0.5)) + 0.3333333333333333*(Poisson(V4|mean=2))))) + 0.5182215743440233*(((0.5246132208157525*((TypeMixtureUnconstrained(REA

In [93]:
print("Accuracy of the inferred statistical types is {}".format(accuracy))
print("Accuracy of the inferred statistical types after 5 iterations is {}".format(accuracy_5))
print("Accuracy of the inferred statistical types after 10 iterations is {}".format(accuracy_10))

Accuracy of the inferred statistical types is 0.4
Accuracy of the inferred statistical types after 5 iterations is 0.4
Accuracy of the inferred statistical types after 10 iterations is 0.8


The results are summarized as follows.

In [139]:
bayesian_acc = {'Dataset_id': ['31', '1464', '334', '50', '333', '1494', '3', '1510', '1489', '37',
                               '1479', '1487', '1063', '1471', '1467', '1480', '1068', '1492', '1050', '1462'],
                'Accuracy_1': [0.524, 1, 0, 0, 0, 0.595, 0.081, 0.838, 0.5, 1, 0.99, 0.931, 0.909, 1, 0.905, 0.545, 1, 0.984, 0.684, 0.4],
                'Accuracy_5': [0.857, 1, 0.428, 0.4, 0.143, 0.285, 0.568, 0.806, 1, 1, 0.99, 0.931, 0.909, 1, 0.905, 0.909, 0.955, 0.984, 0.684, 0.4],
                'Accuracy_10': [0.809, 1, 0.571, 0.7, 0.429, 0.262, 0.703, 0.838, 1, 1, 0.99, 0.876, 0.863, 1, 0.619, 1, 0.955, 0.984, 0.71, 0.8]}
df_bayesian_acc = pd.DataFrame(bayesian_acc) 

In [140]:
df_bayesian_acc[['Dataset_id', 'Accuracy_1', 'Accuracy_5', 'Accuracy_10']]

Dataset_id  Accuracy_1  Accuracy_5  Accuracy_10
0          31       0.524       0.857        0.809
1        1464       1.000       1.000        1.000
2         334       0.000       0.428        0.571
3          50       0.000       0.400        0.700
4         333       0.000       0.143        0.429
5        1494       0.595       0.285        0.262
6           3       0.081       0.568        0.703
7        1510       0.838       0.806        0.838
8        1489       0.500       1.000        1.000
9          37       1.000       1.000        1.000
10       1479       0.990       0.990        0.990
11       1487       0.931       0.931        0.876
12       1063       0.909       0.909        0.863
13       1471       1.000       1.000        1.000
14       1467       0.905       0.905        0.619
15       1480       0.545       0.909        1.000
16       1068       1.000       0.955        0.955
17       1492       0.984       0.984        0.984
18       1050       0.684       0.684        0.710
19       1462       0.400       0.400        0.800

In [134]:
import plotly.plotly as py
import plotly.graph_objs as go

trace0 = go.Bar(
    x=['dataset 31', 'dataset 1464', 'dataset 334', 'dataset 50', 'dataset 333', 'dataset 1494', 'dataset 3', 'dataset 1510', 'dataset 1489', 
       'dataset 37', 'dataset 1479', 'dataset 1487', 'dataset 1063', 'dataset 1471', 'dataset 1467', 'dataset 1480', 'dataset 1068', 
       'dataset 1492', 'dataset 1050', 'dataset 1462'],
    y=bayesian_acc['Accuracy_1'],
    name='1 iteration',
    marker=dict(
        color='rgb(49,130,189)'
    )
)
trace1 = go.Bar(
    x=['dataset 31', 'dataset 1464', 'dataset 334', 'dataset 50', 'dataset 333', 'dataset 1494', 'dataset 3', 'dataset 1510', 'dataset 1489', 
       'dataset 37', 'dataset 1479', 'dataset 1487', 'dataset 1063', 'dataset 1471', 'dataset 1467', 'dataset 1480', 'dataset 1068', 
       'dataset 1492', 'dataset 1050', 'dataset 1462'],
    y=bayesian_acc['Accuracy_5'],
    name='5 iterations',
    marker=dict(
        color='rgb(204,204,204)'
    )
)
trace2 = go.Bar(
    x=['dataset 31', 'dataset 1464', 'dataset 334', 'dataset 50', 'dataset 333', 'dataset 1494', 'dataset 3', 'dataset 1510', 'dataset 1489', 
       'dataset 37', 'dataset 1479', 'dataset 1487', 'dataset 1063', 'dataset 1471', 'dataset 1467', 'dataset 1480', 'dataset 1068', 
       'dataset 1492', 'dataset 1050', 'dataset 1462'],
    y=bayesian_acc['Accuracy_10'],
    name='10 iterations',
    marker=dict(
        color='rgb(107,107,107)'
    )
)


data = [trace0, trace1, trace2]
layout = go.Layout(
    xaxis=dict(tickangle=-45),
    barmode='group',
    yaxis=dict(
        title='Accuracy'
    )
)
fig = go.Figure(data=data, layout=layout)
py.iplot(fig, filename='bayesian_acc')

In [137]:
mean_acc_1 = np.mean(bayesian_acc['Accuracy_1'])
mean_acc_5 = np.mean(bayesian_acc['Accuracy_5'])
mean_acc_10 = np.mean(bayesian_acc['Accuracy_10'])

trace0 = go.Bar(
    x=['1 iteration', '5 iterations', '10 iterations'],
    y=[mean_acc_1, mean_acc_5, mean_acc_10],
    marker=dict(
        color='rgb(158,202,225)',
        line=dict(
            color='rgb(8,48,107)',
            width=1.5,
        )
    ),
    opacity=0.6
)

data = [trace0]
layout = go.Layout(
    title='Mean accuracy after running different iterations of Bayesian model ',
    yaxis=dict(
        title='Mean Accuracy'
    )
)

fig = go.Figure(data=data, layout=layout)
py.iplot(fig, filename='text-hover-bar')

In [138]:
print(mean_acc_1, mean_acc_5, mean_acc_10)

0.6443 0.7577 0.8054500000000001
